# <center>  Data Inversion for Aerosol Science and Technology </center> 

AAAR 2019 Tutorial Notes <br>
Markus Petters (mdpetter@ncsu.edu)<br>
Notes based on Petters et al. (2018, Aerosol Science & Technology) 

## 1. Overview over the differential mobility analyzer

The cylindrical DMA (Knutson and Whitby, 1975) passes a polydisperse aerosol flow through an annulus gap. An electric potential is applied between the inner and outer column. The electric potential drags charged particles through a viscous sheath flow. Particles whose mobility coincide with the electric and flow field forces will be steered to the sample slit. All other particles exit with the excess flow. 

<img src="Figures/nbs1_f01.png" width="400"> 
<b> Figure 1. </b> Schematic of a differential mobility analyzer. The cylindrical differential mobility analyzer is an annular capacitor. The column's properties are defined by the radii $r_1$, $r_2$, the length of the aerosol path, $l$. Operation conditions are defined by the the electric potential $v$ applied across the annulus and the four flow rates: sheath flow, $q_{sh}$, polydisperse aerosol flow $q_a$, excess flow, $q_{ex}$, and monodisperse sample flow, $q_{sa}$. Throughout this work it is assumed that the flows are balanced, i.e. $q_{sh} = q_{ex}$ and $q_{sa} = q_a$. The two flows tracked are $q_{sh}$ and $q_{sa}$. Dimensions and flow range for one commonly used model are provided in Table 1 below. <br>


<center>
<table style="width:45%">
    <caption> <b> Table 1. </b> Geometry of the TSI 3080 long cylindrical DMA column together with typical ranges for operation parameters. </caption>
  <tr>
    <th align="justify">Geometry parameter</th>
    <th align="justify">Value</th> 
    <th align="justify">Operational parameter</th>
    <th align="justify">Range</th> 
</tr>
  <tr>
    <td align="justify">$r_1$</td>
    <td align="justify">9.37×10⁻³ m</td> 
    <td align="justify">$v$</td>
    <td align="justify">± 10-10000 V</td> 
</tr>
  <tr>
    <td align="justify">$r_2$</td>
    <td align="justify">1.961×10⁻² m</td> 
    <td align="justify">$q_{sh}$</td>
    <td align="justify">2-20 L min⁻¹</td> 
</tr>
  <tr>
    <td align="justify">$l$</td>
    <td align="justify">0.44369 m</td> 
    <td align="justify">$q_{sa}$</td>
    <td align="justify">0.3-2 L min⁻¹</td> 
  </tr>
</table>
</center>


### Representing DMAs in code
The Λ structures define the DMAa in terms of flow rates and geometry and power supply polarity. The geometry parameters used in this example correspond to the TSI 3080 long column. The effective diffusion length describes diffusional loss in the DMA column (Reineking & Porstendörfer, 1986) which is described further below. Diffusional loss is ignored if ```leff = 0```. The Λ variable is used in various functions to define the state of the DMA.

The code generates a ```δ``` structure that contains the main language elements for the computations performed in subsequent notebooks. Specifically, it contains the various convolution matrices and defines the size grid in terms of the number of bins and lower and upper diameters. ```Tc``` is the charge efficiency function, ```Tl``` is the penetration efficiency function (see below), ```Z``` are the mobility bin midpoints, ```Dp``` are the diameter bin midpoints (internally in units of nm), ```Ze``` are the mobility bin edges, ```De``` are the diameter bin edges, ```ΔlnD``` is the natural log ratio of upper and lower diameter bin edge, and ```𝐀```, ```𝐒```, and ```𝐎``` are convolution matrices. 

In [49]:
using Plots, Plots.PlotMeasures, DifferentialMobilityAnalyzers, Printf, LsqFit 
using LinearAlgebra, DataFrames, Random, Distributions, LambertW, SpecialFunctions
plotlyjs();  

t,p = 295.15, 1e5                                # Temperature [K], Pressure [Pa]
qsa,β = 1.66e-5, 1/5                             # Qsample [m3 s-1], Sample-to-sheath ratio,
r₁,r₂,l = 9.37e-3,1.961e-2,0.44369               # DMA geometry [m]
leff = 13.0                                      # DMA effective diffusion length [m]
m = 6                                            # Upper number of charges
DMAtype = :cylindrical                           # specify DMA type as cylindrical or radial
Λ = DMAconfig(t,p,qsa,qsa/β,r₁,r₂,l,leff,:-,m,DMAtype)  # Specify DMA with negative polarity
bins,z₁,z₂ = 512, dtoz(Λ,1000e-9), dtoz(Λ,10e-9) # bins, upper, lower mobility limit
δ = setupDMA(Λ, z₁, z₂, bins);                   # Compute matrices
Λp = DMAconfig(t,p,qsa,qsa/β,r₁,r₂,l,leff,:+,m,DMAtype) # Specify DMA with positive polarity
δp = setupDMA(Λp, z₁, z₂, bins);                 # Compute matrices
fieldnames(DifferentialMobilityAnalyzer)         # Print a list of variables constained in δ

(:Ω, :Tc, :Tl, :Z, :Ze, :Dp, :De, :ΔlnD, :𝐀, :𝐒, :𝐎)

## 2. Important Functions 
This block describes (a) the Cunningham slip-flow correction, (b) the particle diffusion coefficient, (c) the relationship between v, zp, and dp, (d) the penetration efficiency of particles transitting through the DMA, (e) the charging efficiency of the bipolar charger, and (f) the transfer function of particles selected by the DMA.
### (a) Cunningham slip-flow correction/mean free path: 
The slip flow correction, $c_c$ [-], accounts for the decreased drag particles experience relative to Stokes' drag force when particle size approaches the scale of the mean free path of air. It is computed following Hinds (1999) Eq. 3.20
<center> $c_c = 1+\frac{\lambda}{d_p} \left(2.34+1.05 \exp \left[-0.39 \frac{d_p}{\lambda}\right]\right)$ </center>
where $d_p$ is the particle diameter and $\lambda = 6.6 \times 10^{-8}\frac{101315}{p}\frac{t}{293.15}$ is the mean free path of air as a function of pressure $p$ [Pa] and temperature $t$ [K]. 

In [50]:
figure("Arial", 2, 3, 2, 8)
Dp = exp10.(range(log10(1e-9), stop=log10(1000e-9), length=1000))
plot(Dp*1e9, cc(Λ,Dp), xscale = :log10, yscale = :log10, xlim = (1, 1000), ylim = (1, 500), yticks = [1, 10], 
    xlabel = "Particle diameter (nm)", color = :black, ylabel = "c<sub>c</sub> (-)", legend = :none, 
    right_margin = 20px)

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 2.</b> Size dependence of Cunningham slip flow correction factor. Also see Hinds (1999) Figure 3.3.

### (b) Particle diffusion coefficient/air viscosity: 
The diffusion coefficient of particles in in air, $d_{ab}$, describes the random displacement of particles due to Brownian motion. Here it is computed via the Stokes-Einstein relation (Hinds, 1999, Eq. 7.20)
<center> $d_{ab} = \frac{k_bTc_c}{3\pi\eta d_p}$ </center>
where $k_b$ is Boltzmann's constant and $\eta = 1.83245\times10^{-5} \exp \left(1.5 \ln \left[\frac{T}{296.1}\right]\right)\left (\frac{406.55}{T+110.4} \right)$ is the viscosity of air [Pa s] as a function of temperature [K]. <br> <br>
The function ```dab(Λ,dp)``` is defined in dmafunctions.jl, where Λ contains pressure and temperature and Dp is a vector of particle diameter in [m] and ```dab(Λ,dp)``` is in [m² s⁻¹].

In [51]:
plot(Dp*1e9, dab(Λ,Dp)*1e4, xscale = :log10, yscale = :log10, xlim = (1, 1000), ylim = (1e-7, 1e-1), 
    label = "d<sub>ab</sub>", color = :black, yticks = [1e-7, 1e-6, 1e-5, 1e-4, 1e-3, 1e-2], 
    ylabel = "d<sub>ab</sub> (cm² s⁻¹ )", xlabel = "Particle diameter (nm)", 
    legend = :none, right_margin = 20px)

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 3. </b> Size dependence of particle diffusion coefficient. Also compare to Hinds Table 7.1.

### (c) Relationship between v, z, and dp: 
For the cylindrical DMA and balanced flows, the relationship between $v$, $z^s$, and $d_p$ is given by Knutson and Whitby (1975)
<center> $z^s = \frac{q_{sh}}{2\pi l v} \ln \left(\frac{r_2}{r_1}\right)$ </center>
where $v$ is the potential applied between the inner and out section of the annulus. The relationship between $d_p$ and $z^s$ is 
<center> $d_p =  \frac{kec_c}{3\pi \eta z^s}$ </center>
where $e$ is the elementary charge and $k$ is the number of charges on the particle. <br> 

The function ```vtov(Λ,v)``` is defined in DifferentialMobilityAnalyzer.jl, where Λ subsumes the DMA geometery (r1,r2,l), sheath flow rate, and t,p to compute $c_c$ and η. The function ```dtoz(Λ,d)``` converts diameter to particle mobility. The function ```ztod(Λ,k,z)``` converts mobility to mobility diameter for particles carrying k charges. This function requires iteration since one of the arguments, cc, also depends on particle diameter. Example conversions using these functions are shown below.

In [52]:
k = 1
v = 1000
z = vtoz(Λ,v)
dp = ztod(Λ,k,z)
@printf("V = %i V corresponds to Z = %.2e []\n", v, z)
@printf("Z = %.2e [] and n = %i charge(s) corresponds to Dp = %i nm\n", z,k,dp)
@printf("Dp = %i nm and n = 1 charge corresponds to Zp = %.2e nm\n", dp,dtoz(Λ,dp*1e-9))

V = 1000 V corresponds to Z = 2.20e-08 []
Z = 2.20e-08 [] and n = 1 charge(s) corresponds to Dp = 114 nm
Dp = 114 nm and n = 1 charge corresponds to Zp = 2.20e-08 nm


### (d) Peneration efficiency through the DMA: 
Penetration efficiency through the DMA is computed based on the parameterized results by Reineking & Porstendörfer (1986).
<center> $T_l = 0.82\exp(-11.5u)+0.1\exp(-70.0u)+0.03\exp(-180.0u)+0.02\exp(-340.0u)$ </center>
where $u = \frac{d_{ab} l_{eff}}{q_{sa}}$, $l_{eff}$ is the parameterized effective diffusion length, and $q_{sa}$ is the aerosol flow rate through the DMA. <br> <br>
The function Tl(Λ,dp) is defined in DifferentialMobilityAnalyzer.jl, where Λ contains the effective length, aerosol flow rate, and $t$,$p$ to compute $d_{ab}$. The particle diameter $d_p$ is in [nm]. To treat multiple DMAs with different {$l_{eff}$, $q_sa$, $t$, $p$} in a single scipt, the function Tl is appropriately embedded in the structure δ.

In [53]:
p3 = plot(Dp*1e9, δ.Tl(Λ,Dp*1e9), xscale = :log10, yscale = :log10, ylim = (0.01, 1), color = :black,
    yticks = [0.01, 0.1, 1.0], ylabel = "T<sub>l</sub> (-)",xlabel = "Particle diameter (nm)",  
    legend = :none, right_margin = 20px)

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 4. </b> Size dependence of penetration efficiency through the DMA for $l_{eff}$ specified above. Note that the function ```δ.Tl(Λ,Dp*1e9)``` takes diameter in units of nm. Also compare to Figure 2 in Reineking and Porstendorfer (1986).

### (e) Charging efficiency: 
Charging efficiency (charge equilibrium) obtained in the bipolar charger is computed based on the parameterized measurements by Wiedensohler et al. (1988) with coefficients taken from the TSI 3080 Manual (2009). 
<center> $T_c(k) = 10^\left\{ \sum_{i=1}^6 a_i (k) \left[ \ln \left(\frac{D_p}{nm}\right) \right]^{i-1} \right \}$ </center>
where $k = -2,-1,1,2$ is the number and polarity of particle charge and $a_i$ are empirical coefficients. <br> <br>
The function Tc(k) is defined in module DifferentialMobilityAnalyzer.jl. It return the charging efficiency for n charges. Each function belongs to a DMA structure, which sets the internal diameter grid and polarity. In this script, the function δ.Tc is for negative polarity and δp.Tc for positive polarity as defined above. The function is computes charging efficiencies on the DMA internal grid δ.dp, which is set by the mobility range and the number bins.

In [54]:
println("Table 1. Coefficients aᵢ(n) for negative (n) and positive (p) charging efficiency");
DifferentialMobilityAnalyzers.ax

Table 1. Coefficients aᵢ(n) for negative (n) and positive (p) charging efficiency


6×4 DataFrame
│ Row │ n2       │ n1      │ p1      │ p2       │
│     │ Float64  │ Float64 │ Float64 │ Float64  │
├─────┼──────────┼─────────┼─────────┼──────────┤
│ 1   │ -26.3328 │ -2.3197 │ -2.3484 │ -44.4756 │
│ 2   │ 35.9044  │ 0.6175  │ 0.6044  │ 79.3772  │
│ 3   │ -21.4608 │ 0.6201  │ 0.48    │ -62.89   │
│ 4   │ 7.0867   │ -0.1105 │ 0.0013  │ 26.4492  │
│ 5   │ -1.3088  │ -0.126  │ -0.1553 │ -5.748   │
│ 6   │ 0.1051   │ 0.0297  │ 0.032   │ 0.5049   │

For $k \ge \pm 3$, the formula from the TSI manual is used:
<center> $T_c(k) = \frac{e}{\sqrt{4\pi^2\epsilon D_pk_bT}} \exp \left( \frac{-\frac{\left[|k| - 2\pi\epsilon D_pk_bT \ln(0.875)\right]^2}{e^2}}{ \frac{4\pi\epsilon D_pk_bT}{e^2}} \right) $</center>
where $e$ is the elementary charge and $\epsilon$ is the dielectric constant for air.

In [55]:
plot(δ.Dp, δ.Tc(1,δ.Dp), xscale = :log10, yscale = :log10, ylim = (0.002, 0.5), color = :black, xlim = (10,1000),
    yticks = [0.01, 0.1, 1.0], ylabel = "T<sub>c</sub> (-)",xlabel = "Particle diameter (nm)", label = "k = +1",)
plot!(δ.Dp,   δ.Tc(2,δ.Dp), label = "k = +2", color = :black, ls = :dash)
plot!(δ.Dp,  δp.Tc(1,δ.Dp), label = "k = -1", color = RGBA(0.8,0,0,1))
plot!(δp.Dp, δp.Tc(2,δ.Dp), label = "k = -2", color = RGBA(0.8,0,0,1), ls = :dash)
plot!(δp.Dp, δp.Tc(3,δ.Dp), label = "k = ±3", color = RGBA(0,0,0.8,1))
plot!(δp.Dp, δp.Tc(4,δ.Dp), label = "k = ±4", color = RGBA(0.6,0,0.6,1))

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 5. </b> Size dependence of fractional charging efficiency of through the bipolar charger. Also see Figure B6 and Table B1 in the TSI Manual (2009).

### (f) DMA transfer function
The DMA transfer function is the probability that a particle of a particle of a given size exits the classifier via the sample flow. The diffusive broadened DMA transfer function is computed assuming blanced sheath and excess flows using the expression of Stolzenburg and McMurry (2008).
<center> $ \Omega(\tilde{z},\beta,\sigma) = \frac{\sigma}{\sqrt{2}\beta}\left[\epsilon \left( \frac{\tilde{z}-(1+\beta)}{\sqrt{2}\sigma} \right) + \epsilon \left (\frac{\tilde{z}-(1-\beta)}{\sqrt{2}\sigma} \right) - 2\epsilon \left ( \frac{\tilde{z}-1}{\sqrt{2}\sigma}\right)  \right]$ </center>
    
where $\tilde{z} = \frac{z}{z^s}$ is the dimensionless mobility, $z$ is the particle mobility $z^s$ is the centroid mobility selected by the DMA, $\epsilon = x \mathrm{erf}(x) +\left(\exp(-x^2)/\sqrt{\pi}\right)$, $\mathrm{erf}$ is the error function, and $\beta = \frac{q_{sa}}{q_{sh}}$. The parameter $\sigma$ accounts for diffusional broading of the transfer function. Assuming plug flow, $\sigma$ can be computed using the following equations Hagwood (1999) <br> <br>
$\gamma = \left(\frac{r_1}{r_2}\right)^2$ <br>
$I = \frac{1}{2}(1+γ)$ <br>
$\kappa = \frac{lr_2}{r_2^2-r_1^2}$ <br>
$G = \frac{4(1+\beta)^2}{(1-γ)} \left[I+\{2(1+\beta)\kappa\}^{-2} \right ] $<br>
$\sigma = \sqrt{\frac{2G\pi ld_{ab}}{q_{sh}}}$ <br> <br>
The function ```δ.Ω(Λ,z,zˢ)``` is implemented in dmafunctions.jl. Inputs include a DMA structure that conveys {t, p, and flow rates}, a mobility vector scalar z or vector Z, and a centroid mobility zˢ . 	

In [56]:
Z = exp10.(range(log10(1e-9), stop=log10(1e-6), length=1000)) # Fine grain mobility grid 
zˢ = dtoz(Λ, 200e-9)                           # Convert diameter to mobility
plot(Z/zˢ, δ.Ω(Λ,Z,zˢ), ylabel = "Ω (-)", xlim = (0.7, 1.3), ylim = (0,1), 
    xlabel = "z/Z <sup>s</sup> (-)", color = :black,
    left_margin = 33px, label = "Dp = 200 nm", 
    xticks = [0.7, 0.8, 0.9, 1.0, 1.1, 1.2, 1.3])
zˢ = dtoz(Λ, 20e-9)
p4 = plot!(Z/zˢ, δ.Ω(Λ,Z,zˢ), label = "Dp = 20 nm", color = RGBA(0.8,0,0,1))

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 6. </b> Example normalized DMA transfer function for flow ratio $\beta$ = 1/5 and 20 and 200 nm particles. Also see to Fig. 2 and Fig. 4 in Stolzenburg and McMurry (2008).

## 3. Representation of the (lognormal) size distribution
The multi-modal lognormal size distribution is given by (e.g. Seinfeld and Pandis, 2006)
<center> $\frac{dN}{d\ln D_p} = \sum_{i=1}^n \frac{N_{t,i}}{\sqrt{2\pi}\ln\sigma_{g,i}} \exp \left(- \frac{\left[\ln D_p-\ln D_{pg,i}\right]^2}{2\ln \sigma_{g,i}^2}\right) $  </center>
where $\frac{dN}{d\ln D_p}$ is the spectral number density, $N_{t,i}$ is the total number concentration, $\sigma_{g,i}$ is the geometric standard deviation, and $D_{pg,i}$ is the geometric mean diameter of the $i^{th}$ mode, and $n$ is the number of modes. <br> 

The function ```lognormal(A; D1 = D1, D2 = D2, bins = n)``` is defined in aerosolsizedistribution.jl and generates a discrete lognormal size distribtution between diameters D1 and D2 with n bins. A is an array of modes allowing to specify an arbitrary number of modes for the distribution, e.g. ```A = [[Nt1, Dpg1,σ1], [Nt2, Dpg2,σ2], ...]```. The function returns a structure of type SizeDistribution, that represents the discrete distribution as shown in the Table below.

In [57]:
r = x->Int.(round.(x, digits = 0))  # Function to round and convert to Int
𝕟 = lognormal([[200, 80, 1.2]]; d1 = 30.0, d2 = 300.0, bins = 10); 
DataFrame(Dlow = r(𝕟.De[1:end-1]),Dup = r(𝕟.De[2:end]),ΔlnD = round.(𝕟.ΔlnD,digits=2),
    Dp = r(𝕟.Dp), S = r(𝕟.S),N = r(𝕟.N))

10×6 DataFrame
│ Row │ Dlow  │ Dup   │ ΔlnD    │ Dp    │ S     │ N     │
│     │ Int64 │ Int64 │ Float64 │ Int64 │ Int64 │ Int64 │
├─────┼───────┼───────┼─────────┼───────┼───────┼───────┤
│ 1   │ 30    │ 38    │ 0.23    │ 34    │ 0     │ 0     │
│ 2   │ 38    │ 48    │ 0.23    │ 42    │ 1     │ 0     │
│ 3   │ 48    │ 60    │ 0.23    │ 53    │ 37    │ 9     │
│ 4   │ 60    │ 75    │ 0.23    │ 67    │ 276   │ 64    │
│ 5   │ 75    │ 95    │ 0.23    │ 85    │ 418   │ 96    │
│ 6   │ 95    │ 119   │ 0.23    │ 106   │ 128   │ 30    │
│ 7   │ 119   │ 150   │ 0.23    │ 134   │ 8     │ 2     │
│ 8   │ 150   │ 189   │ 0.23    │ 169   │ 0     │ 0     │
│ 9   │ 189   │ 238   │ 0.23    │ 212   │ 0     │ 0     │
│ 10  │ 238   │ 300   │ 0.23    │ 267   │ 0     │ 0     │

<b> Table 2. </b> Example representation of a lognormal aerosol size distribution on a 10-bin geometrically stepped grid ranging from 30 to 300 nm with geometric standard deviation 1.2 and total number concentration 200 cm⁻³ . Column 1 gives the bin number, Dlow is the lower bin diameter, Dup is the upper bin diameter, ΔlnD = ln(Dup) - ln(Dlow), Dp = $\sqrt{Dup \cdot Dlow}$ is the geometric midpoint diameter of the bin, S $\equiv \frac{dN}{d\ln Dp}$ is the number spectral density [cm⁻³] and N = $\frac{dN}{d\ln Dp} \cdot d\ln Dp$ is the number concentration in each bin [cm⁻³]. The total number concentration is recovered by summing over all bins, i.e. Nt = $\sum_{i=1}^{10} N$. For a geometrically stepped grid, the ΔlnD is identical in each bin. Numbers are rounded for clarity. 

In [58]:
# Generate a lognormal size distribution that serves as input. 
#   - Nt is in [# m-3] for calculations with k12
#   - Dg is in nm in accordance with the grid uings
#   - σ is the geometeric standard deviation (σ > 1)
# Multiple modes can be defined by concatenation. A single mode is permissible A = [[Nt1,Dg1,σ1]]
𝕟 = lognormal([[130, 50, 1.3], [340, 120, 1.9]]; d1 = 10.0, d2 = 1000.0, bins = 256); 

figure("Arial", 2, 3, 2, 8)
p = plot(𝕟.Dp, 𝕟.S, xaxis = :log10, xticks = [10, 100, 1000], legend = :none, right_margin = 35px,
    ylabel = "dN/dlnD (cm⁻³)", xlim = (8,1000), color =  :black, xlabel = "Diameter (nm)")

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 7. </b> Two mode lognormal size distribution for $N_{t,1} = 130\; cm^{-3}$, $D_{pg,1} = 50\; nm$,  $\sigma_{g,1} = 1.3$, $N_{t,2} = 340\; cm^{-3}$, $D_{pg,2} = 120\; nm$ amd  $\sigma_{g,1} = 1.9$.

### (a) Addition of two size distributions
Let 𝕟₁ and 𝕟₂ denote a two size distribution defined on the same diameter grid. Then
```julia
𝕩 = 𝕟₁+𝕟₂ 
```
is defined such that 
```julia
𝕩.S = 𝕟₁.S + 𝕟₂.S 
𝕩.N = 𝕩.S.*𝕟₁.ΔlnD 
```
The net result is the superposition of size distributions.

In [59]:
figure("Arial", 2, 5.5, 2, 8)
𝕟₁ = lognormal([[120, 90, 1.10]]; d1 = 10.0, d2 = 1000.0, bins = 256);  # size distribution
𝕟₂ = lognormal([[90, 140, 1.15]]; d1 = 20.0, d2 = 800.0, bins = 64);    # size distribution
𝕩 = 𝕟₁+𝕟₂   # Example addition, note the mismatch of the grid 

p1 = plot(𝕟₁.Dp, 𝕟₁.S, xaxis = :log10, xticks = [10, 100, 1000], lt = :steppre,
    label = "𝕟₁", ylabel = "dN/dlnD (cm⁻³)", xlim = (40,400), color =  :black,
    xlabel = "Diameter (nm)", right_margin = 25px)
p1 = plot!(𝕟₂.Dp, 𝕟₂.S, xaxis = :log10, label = "𝕟₂", lt = :steppre, color = RGBA(0.8,0,0,1))

p2 = plot(𝕩.Dp, 𝕩.S, xaxis = :log10, label = "𝕩 = 𝕟₁+𝕟₂", xlabel = "Diameter (nm)",
    color = RGBA(0.6,0,0.6,1), lt = :steppre, ylabel = "dN/dlnD (cm⁻³)", xlim = (40,400))

@printf("Nt1 = %i, Nt2 = %i, sum(𝕩.N) = %i", sum(𝕟₁.N), sum(𝕟₂.N), sum(𝕩.N))
plot(p1,p2, grid = (1,2),left_margin = 20px)

Nt1 = 120, Nt2 = 90, sum(𝕩.N) = 210

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 8. </b> Illustration of the operator 𝕟₁+𝕟₂. The operation intuitively superimposed the two distributions into a single distribution. As shown in the example, the two 𝕟₁+𝕟₂ distributions do not share the same grid. In case of a grid mismatch, the new size distribution will use the grid for 𝕟₁.

### (b) Multiplication of  vector and size distribution
Let T denote a 1D vector that has the same number of elements as the size distribution $𝕟$. Then
```julia
𝕩 = T * 𝕟 
```
is defined such that 
```julia
𝕩.N = T * 𝕟.N
𝕩.S = T * 𝕟.S
```
The operator $*$ denotes elementwise multiplication (or broadcasting in Julia terminology). The net result is a bin-by-bin scaling of the number concentration. 

In [60]:
𝕟 = lognormal([[100, 100, 1.1]]; d1 = 10.0, d2 = 1000.0, bins = 256);  # size distribution
μ,σ = 100.0, 100.0
T = 0.5*(1.0 .+ erf.((𝕟.Dp .- μ)./(sqrt(2σ)))) # Simple error function with mean μ and std. dev σ
𝕩 = T*𝕟                                        # Example multiplication

p1 = plot(𝕟.Dp, T, xaxis = :log10, label = "T(𝕟.dp)", ylabel = "Fraction (-)", ylim = (0,1),
    color = RGBA(0.6,0,0.6,1), lt = :steppre, xlabel = "Diameter (nm)")
p2 = plot(𝕟.Dp, 𝕟.S, xaxis = :log10, lt = :steppre, right_margin = 25px, color =  :black,
    label = "𝕟", ylabel = "dN/dlnD (cm⁻³)", xlim = (40,400), xlabel = "Diameter (nm)")
p2 = plot!(𝕩.Dp, 𝕩.S, xaxis = :log10, label = "𝕩 = T.*𝕟", color = RGBA(0.8,0,0,1), lt = :steppre)
plot(p1,p2, grid = (1,2),left_margin = 20px)

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 9. </b> Illustration of the operator T$*$𝕟. The array T is defined for each diameter point of the distribution. The convolution 𝕩 = T$*$𝕟 also applies to number concentration (not shown).

### (c) Dot product of scalar and size distribution
Let a denote a floating point scalar and $𝕟$ denote a size distribution. Then
```julia
𝕩 = a⋅𝕟
```
is defined such that 
```julia
𝕩.Dp = a*𝕟.Dp 
```
The net result is a uniform diameter shift of the size distribution.

In [61]:
a = 2.0 # Note that a must be a floating point number
𝕟 = lognormal([[100, 100, 1.1]]; d1 = 10.0, d2 = 1000.0, bins = 256);  # size distribution
𝕩 = a⋅𝕟 

p1 = plot(𝕟.Dp, 𝕟.S, xaxis = :log10, lt = :steppre, label = "𝕟", ylabel = "dN/dlnD (cm⁻³)", 
    xlim = (40,400), color =  :black, xlabel = "Diameter (nm)", right_margin = 25px)
p1 = plot!(𝕩.Dp, 𝕩.S, xaxis = :log10, label = "𝕩 = a⋅𝕟",  color = RGBA(0.8,0,0,1), lt = :steppre)

p2 = plot(𝕟.Dp, 𝕟.N, xaxis = :log10, xticks = [10, 100, 1000], lt = :steppre, label = "𝕟", 
    ylabel = "Concentration (cm⁻³)", xlim = (40,400), color =  :black, xlabel = "Diameter (nm)", 
    right_margin = 25px, ls = :dashdot)
p2 = plot!(𝕩.Dp, 𝕩.N, xaxis = :log10, label = "𝕩 = a⋅𝕟", ls = :dashdot, color = RGBA(0.8,0,0,1), lt = :steppre)

plot(p1,p2, grid = (1,2),left_margin = 20px) 

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 10. </b> Illustration of the operator a⋅𝕟. The operation intuitively shifts the size distribution by a factor of two. Note, however, that the underlying diameter grid remains unchanged. This is achieved by interpolating the shifted size distribution back onto the original diameter grid. For this reason, the final fields dp and de are unaltered.  

### (d) Multiplication of  matrix and size distribution
Let <b>A</b> denote a $n\times n$ matrix where $n$ equals the number of size bins of $𝕟$. Then
```julia
𝕩 = 𝐀*𝕟 
```
is defined such that 
```julia
𝕩.N = 𝐀*𝕟.N
𝕩.S = 𝐀*𝕟.S
```
The operator $*$ denotes matrix multiplication. 

In [62]:
𝕟 = DMALognormalDistribution([[130, 50, 1.3], [280, 140, 1.9]],δ);
𝕩 = δ.𝐀*𝕟 

p1 = plot(𝕟.Dp, 𝕟.S, xaxis = :log10, xticks = [10, 100, 1000], legend = :none, 
    ylabel = "dN/dlnD (cm⁻³)", xlim = (8,1000), color =  :black, xlabel = "Diameter (nm)", 
    right_margin = 35px, lt = :steppre)

p2 = plot(𝕩.Dp, 𝕩.N, legend = :none,  xaxis = :log10, right_margin = 35px, lt = :steppre,
    ylabel = "Concentration (cm⁻³)", xlim = (8,1000), color =  :black, xlabel = "Diameter (nm)")

plot(p1,p2,grid=(1,2))

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 11. </b> Illustration of the operator <b>A</b>$*$𝕟. The matrix <b>A</b> is the convolution matrix defined in Notebook S02. The convolution 𝕩 = <b>A</b>$*$𝕟 also applies to S (not shown).

## 4. Transmission through the DMA at Constant Voltage

Figure 12 shows a schematic instrument setup with an array of detectors. The DMA is operated in classifier mode and set to a single voltage. The mobility classified particles are then passed to one or more detectors. 
<img src="Figures/nbs2_f01.png" width="350" align = "middle">
<figcaption><b> Figure 12. </b> Illustration of the combined transfer function through the DMA. </figcaption> 


In [63]:
Dm = 100.0                   # Size select 100 nm mobility diameter
zˢ = dtoz(Λ, Dm*1e-9);       # Compute corresponding electrical mobility
Dp = map(k->ztod(Λ,k,zˢ), 1:Λ.m)
@printf("The +1, +2, and +3 selected diameters are %3.0f, %3.0f, and %3.0f nm\n", Dp[1],Dp[2],Dp[3])

T = (zˢ,k,Λ,δ) -> δ.Ω(Λ,δ.Z,zˢ/k).*δ.Tc(k,δ.Dp).*δ.Tl(Λ,δ.Dp);  # DMA Transmission

Ax = [[600., 60., 1.9], [900., 210., 1.9]]  # [[Nt1,Dg1,σ1],[Nt1,Dg1,σ1], ....]
𝕟ᶜⁿ = DMALognormalDistribution(Ax, δ);      # Returns the size distribution 
ℕ = map(k -> T(zˢ,k,Λ,δ)*𝕟ᶜⁿ,1:Λ.m)                                # ℕ[k] : Mob. size distribution +k charges
𝕄 = map(k -> (ztod(Λ,1,zˢ)/ztod(Λ,k,zˢ))⋅(T(zˢ,k,Λ,δ)*𝕟ᶜⁿ),1:Λ.m) # 𝕄[k] : App. Mob. distribution +k charges 
𝕟ₜ, 𝕞ₜ = sum(ℕ), sum(𝕄)

figure("Arial", 2, 5.5, 1.7, 8)

# Get a list of colors from the theme palette
p = Plots.get_color_palette(:auto, default(:bgcolor), 100)

# Size distribution
pre = 1e-2
p1 = plot(𝕟ᶜⁿ.Dp, pre*𝕟ᶜⁿ.S, xaxis = :log10, xticks = [10, 100, 1000], ylabel = "dN/dlnD × 10⁻² (cm⁻³)", 
    label = "𝕟ᶜⁿ", color = :black,left_margin = 20px, xlabel = "Mobility Diameter (nm)",
    ylim = (0,6.5))

# Mobility distribution
p2 = plot(𝕄[1].Dp,pre*𝕄[1].S,  xlim = (70,150), label = "𝕄₁", xtick = [80,100,120, 140],
     ytick = [0,0.5,1, 1.5], ylim = (0,1.6), xlabel = "Apparent +1 Mobility Diam. (nm)")
p2 = plot!(𝕄[2].Dp,pre*𝕄[2].S, label = "𝕄₂")   
p3 = plot!(𝕄[3].Dp,pre*𝕄[3].S, label = "𝕄₃")   
p2 = plot!(𝕞ₜ.Dp,pre*𝕞ₜ.S, ls = :dashdot, color = :black, label = "𝕞ₜ")   

# Size distribution
p3 = plot(ℕ[1].Dp,pre*ℕ[1].S, xlim = (70,250), label = "ℕ₁", ytick = [0,0.5,1,1.5],
     xlabel = "Mobility Diameter (nm)", ylim = (0,1.6))
p3 = plot!(ℕ[2].Dp,pre*ℕ[2].S, label = "ℕ₂")   
p3 = plot!(ℕ[3].Dp,pre*ℕ[3].S, label = "ℕ₃")   
p3 = plot!(𝕟ₜ.Dp,pre*𝕟ₜ.S, ls = :dashdot, color = :black, label = "𝕟ₜ", right_margin = 15px)   

plot(p1,p2,p3, layout = grid(1,3), legend=:right, top_margin = 18px, lw = 2)

The +1, +2, and +3 selected diameters are 100, 151, and 195 nm


<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 13. </b> Left: assumed bimodal lognormal size distribution. Middle: monodisperse mobility size distribution. Dashed line is total number concentration. Blue, organge, and green lines represent the contribution of +1, +2, and +3 charges to the size selection. 

In [64]:
units = ["","cm⁻³","μm² cm⁻³","μm³ cm⁻³","","cm⁻³","μm² cm⁻³","μm³ cm⁻³"]
Apre = π*(𝕞ₜ.Dp*1e-3).^2       # prefactor in μm² cm⁻³
Vpre = (π*(𝕞ₜ.Dp*1e-3).^3)/6   # prefactor in μm³ cm⁻³

Label = [units[1], "+1", "+2", "+3", "Total", "Approximation"]
Nₘₒ = [units[2]; round.([sum(𝕄[1].N), sum(𝕄[2].N), sum(𝕄[3].N), sum(𝕞ₜ.N), NaN], digits=1)]
Aₘₒ = [units[3]; round.([sum(Apre.*𝕄[1].N), sum(Apre.*𝕄[2].N), sum(Apre.*𝕄[3].N), 
                sum(Apre.*𝕞ₜ.N), π*(Dm*1e-3)^2*sum(𝕞ₜ.N)],digits=2)]
Vₘₒ = [units[4]; round.([sum(Vpre.*𝕄[1].N), sum(Vpre.*𝕄[2].N), sum(Vpre.*𝕄[3].N), 
                        sum(Vpre.*𝕞ₜ.N), π*(Dm*1e-3)^3*sum(𝕞ₜ.N)/6],digits=4)]

Blank = ["","","","","",""]

Ap = [π*(ℕ[1].Dp*1e-3).^2, π*(ℕ[2].Dp*1e-3).^2, π*(ℕ[3].Dp*1e-3).^2, π*(𝕟ₜ.Dp*1e-3).^2] # prefactor μm² cm⁻³
Vp = [(π*(ℕ[1].Dp*1e-3).^3)/6, (π*(ℕ[2].Dp*1e-3).^3)/6, (π*(ℕ[3].Dp*1e-3).^3)/6, (π*(𝕟ₜ.Dp*1e-3).^3)/6] 

Nₜᵣᵤₑ = [units[6]; round.([sum(ℕ[1].N), sum(ℕ[2].N), sum(ℕ[3].N), sum(𝕟ₜ.N), NaN],digits=1)]
Aₜᵣᵤₑ = [units[7]; round.([sum(Ap[1].*ℕ[1].N), sum(Ap[2].*ℕ[2].N), sum(Ap[3].*ℕ[3].N), 
                           sum(Ap[4].*𝕟ₜ.N), π*(Dm*1e-3)^2*sum(𝕟ₜ.N)],digits=2)]
Vₜᵣᵤₑ = [units[8]; round.([sum(Vp[1].*ℕ[1].N), sum(Vp[1].*ℕ[2].N), sum(Vp[3].*ℕ[3].N), 
                           sum(Vp[4].*𝕟ₜ.N), π*(Dm*1e-3)^3*sum(𝕟ₜ.N)/6],digits=4)]

DataFrame(Label=Label, Nₘₒ=Nₘₒ, Aₘₒ=Aₘₒ, Vₘₒ=Vₘₒ, Blank=Blank, Nₜᵣᵤₑ=Nₜᵣᵤₑ, Aₜᵣᵤₑ=Aₜᵣᵤₑ, Vₜᵣᵤₑ=Vₜᵣᵤₑ)

6×8 DataFrame. Omitted printing of 1 columns
│ Row │ Label         │ Nₘₒ  │ Aₘₒ      │ Vₘₒ      │ Blank  │ Nₜᵣᵤₑ │ Aₜᵣᵤₑ    │
│     │ String        │ Any  │ Any      │ Any      │ String │ Any   │ Any      │
├─────┼───────────────┼──────┼──────────┼──────────┼────────┼───────┼──────────┤
│ 1   │               │ cm⁻³ │ μm² cm⁻³ │ μm³ cm⁻³ │        │ cm⁻³  │ μm² cm⁻³ │
│ 2   │ +1            │ 13.2 │ 0.42     │ 0.0072   │        │ 13.2  │ 0.42     │
│ 3   │ +2            │ 4.2  │ 0.13     │ 0.0023   │        │ 4.2   │ 0.3      │
│ 4   │ +3            │ 1.2  │ 0.04     │ 0.0006   │        │ 1.2   │ 0.14     │
│ 5   │ Total         │ 18.9 │ 0.61     │ 0.0103   │        │ 18.9  │ 0.94     │
│ 6   │ Approximation │ NaN  │ 0.59     │ 0.0099   │        │ NaN   │ 0.59     │

<b> Table 3. </b> Computed number concentration, surface area, and volume from the distributions in Figure 8, middle panel (mobility diameter distributions) and right panel true diameter distributions. For this case, the true surface area and volume are ~50% and ~100% larger than the naive approximation. 

In [65]:
T = (zˢ,k,Λ,δ) -> δ.Ω(Λ,δ.Z,zˢ/k).*δ.Tc(k,δ.Dp).*δ.Tl(Λ,δ.Dp)
Nz = zˢ -> Σ(k->T(zˢ,k,Λ,δ)*𝕟ᶜⁿ, Λ.m)
Az = zˢ -> (π.*(𝕟ᶜⁿ.Dp .* 1e-3).^2) * (Σ(k->T(zˢ,k,Λ,δ)*𝕟ᶜⁿ, Λ.m))
Vz = zˢ -> (π/6.0*(𝕟ᶜⁿ.Dp*1e-3).^3) * (Σ(k->T(zˢ,k,Λ,δ)*𝕟ᶜⁿ, Λ.m))

Dp = map(k->ztod(Λ,k,zˢ), 1:Λ.m)
zˢ = dtoz(Λ, Dm*1e-9)  # Compute corresponding electrical mobility
𝕟ᴺ = Nz(zˢ)            # Number distribution
𝕟ᴬ = Az(zˢ)            # Area distribution
𝕟ⱽ = Vz(zˢ)            # Volume distribution

figure("Arial", 2, 5, 3, 8)

p1 = plot(𝕟ᴺ.Dp, 𝕟ᴺ.S, xticks = round.(Dp,digits=0), ylabel = "dN/dlnD", color = RGBA(0,0,0.8,1),
    label = "𝕟ᴺ (cm⁻³)", left_margin = 20px, xlim = (80,330), lw = 1.5)

p2 = plot(𝕟ᴬ.Dp, 𝕟ᴬ.S, xticks = round.(Dp,digits=0), ylabel = "dA/dlnD", 
    label = "𝕟ᴬ (μm² cm⁻³)", left_margin = 20px,  color = RGBA(0.8,0,0,1),
    xlim = (80,330), lw = 1.5)

p3 = plot(𝕟ⱽ.Dp, 𝕟ⱽ.S, xticks = round.(Dp,digits=0), ylabel = "dV/dlnD", 
    label = "𝕟ⱽ (μm³ cm⁻³)", left_margin = 20px, xlabel = "Mobility Diameter (nm)", 
    color = RGBA(0.5,0,0.5,1), xlim = (80,330), yticks = [0, 0.02, 0.04], lw = 1.5)

plot(p1,p2,p3, layout = grid(3,1), legend=:right, top_margin = 15px)

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 14.</b> Number, surface area, and volume distributions of a single selected mobility, where calculations are carried out up to +6 charges. The tickmarks/gridlines correspond to the selected +1, +2, +3, +4, +5, and +6 diameter. 

# 4. Inversion of Size Distribution Data

Let R be a measured response vector from a DMA. What is the measured true size distribution?

<img src="Figures/nbs2_f02.png" width="750" align = "middle">
<b> Figure 10. </b> Convolution of true size distribution resulting in the response vector.

For situations where instrument noise is neglible, $\epsilon_i \approx 0$ and 
<center> $ \rm{𝕣} = \bf{A}\rm{𝕟}$ </center><br>
In this case, the number concentration is readily obtained from a simple inversion
<center> $ \rm{𝕟} = \bf{A^{-1}}\rm{𝕣}$ </center><br>
This linear matrix inversion approach can be sufficient in some cases, However, even seemingly small noise  is amplified leading to unusable estimates of $\rm{𝕟}$ (e.g., Kandlikar and Ramachandran, 1999). Some method to dampen the noise is needed. This is a achieved via regularization. Several regularization approaches are available for this task (Kandlikar and Ramachandran, 1999). Here the Twomey inverse (Twomey, 1963) together with the L-curve method (Hansen, 2000) is applied to find the optimal regularization parameter. <br>

Routines for regularization are contained in regularization.jl. The method reproduced below is taken from Hansen (2000). The inverse of 𝕣 is found as follows. The residual norm and size of the regularized system are defined as <br>
<center> $L_1 = \left\lVert \bf{A}\rm{𝕟} - \rm{𝕣}\right\rVert_2$ <br>
 $L_2 = \left\lVert \bf{L}(\rm{𝕟} - \rm{𝕟_i})\right\rVert_2$</center>
where $\left\lVert x \right\rVert_2$ denotes the 2-norm of a vector ($x$), $L_1$ and $L_2$ are the residual norm and size of the regularized system, $\bf{A}$ is the forward matrix, $\bf{L}$ is a weights matrix, and $𝕟_i$ is the initial guess of the correct solution. The general inverted size distribution $𝕟_{inv}$ is found via <br>
<center> $𝕟_{inv} = \arg \min\{L_1^2 + \lambda^2 L_2^2\}$ </center> <br>
where $\lambda$ is the regularization parameter and $\arg \min$ indicates the solution from a minimization algorithm. For the special case where $\bf{A}$ is square and $\bf{L} = \bf{I}$ equals the identity matrix, $𝕟_{inv}$ can be obtained without the need for computationally expensive minimization
<center> $𝕟_{inv} = (\bf{A}^\rm{T}\bf{A} + \lambda^\rm{2} \bf{I})^\rm{-1}(\bf{A}^\rm{T} \rm{𝕣} - \lambda^2\bf{S}^{-1} \rm{𝕣})$ </center><br>
 where the initial guess is taken to be $𝕟_i = \bf{S}^{-1}𝕣$ and $\bf{S}$ is obtained by summing the rows of $\bf{A}$ and placing the results on the diagonal of $\mathbf{S}$ (Talukdar and Swihart, 2010). The optimal $\lambda_{opt}$ is found using the L-curve method. The L-curve is defined as a plot of $\log(L_1)$ vs.  $\log(L_2)$, where $L_1$ and $L_2$ are obtained for a series of discrete $\lambda$ values. The $\lambda_{opt}$ is found at the corner of the L-curve, which is mathematically defined as the point where where the curvature of the L-curve is maximum. Here the corner of the L-curve is found using the iterative algorithm described in Talukdar and Swihart (2010). The curvature is calculated using Eq. (14) in Hansen (2000), which requires the first and second derivatives of $d\ln(L_i)^2/d\lambda$. These derivatives of $d\ln(L_i)^2/d\lambda$ are estimated using the Calculus.jl package and defined in regularization.jl<br>


In [66]:
t,p = 295.15, 1e5                                # Temperature [K], Pressure [Pa]
qsa,β = 1.66e-5, 1/5                             # Qsample [m3 s-1], Sample-to-sheath ratio,
r₁,r₂,l = 9.37e-3,1.961e-2,0.44369               # DMA geometry [m]
leff = 13.0                                      # DMA effective diffusion length [m]
m = 6                                            # Upper number of charges
Λ = DMAconfig(t,p,qsa,qsa/β,r₁,r₂,l,leff,:-,m,:cylindrical)   # Specify DMA with negative polarity
bins,z₁,z₂ = 120, dtoz(Λ,1000e-9), dtoz(Λ,10e-9) # bins, upper, lower mobility limit
δ = setupDMA(Λ, z₁, z₂, bins);                   # Compute matrices

### (a) Computation of Convolution Matrix

```julia
Σ = (f,i) -> mapreduce(f,+,1:i)
T = (zˢ,k,Λ,δ) -> δ.Ω(Λ,δ.Z,zˢ/k).*δ.Tc(k,δ.Dp).*δ.Tl(Λ,δ.Dp)
𝐀=(hcat(map(zˢ->Σ(k->T(zˢ,k,Λ,δ),Λ.m),δ.Z)...))'
```

The segements below explain the commands step-by-step. As demonstrated above
```julia 
T = (zˢ,k,Λ,δ) -> δ.Ω(Λ,δ.Z,zˢ/k).*δ.Tc(k,δ.Dp).*δ.Tl(Λ,δ.Dp)
```
selects for a single mobility zˢ and charge k. The function 
```julia
Σ = (f,i) -> mapreduce(f,+,1:i)```
sums functions that take a single argument and apply it for the array 1:i. For example Σ(x->x^2,4) = 1^2 + 2^2 + 3^2 + 4^2 = 30 or Σ(exp,2) = exp(1) + exp(2) = 10.107. In the context above 
```julia 
y = Σ(k->T(zˢ,k,Λ,δ),3)
```
will compute ```T(zˢ,1,Λ,δ)+T(zˢ,2,Λ,δ)+T(zˢ,3,Λ,δ)``` and return an array of transmission efficiencies.

In [67]:
T = (zˢ,k,Λ,δ) -> δ.Ω(Λ,δ.Z,zˢ/k).*δ.Tc(k,δ.Dp).*δ.Tl(Λ,δ.Dp)
𝐀 = (hcat(map(zˢ->Σ(k->T(zˢ,k,Λ,δ),Λ.m),δ.Z)...))'

120×120 Adjoint{Float64,Array{Float64,2}}:
 0.100718     0.0695514    0.0341323    …  0.0          0.0        
 0.0703494    0.102528     0.0709314       5.96839e-71  3.79147e-14
 0.0410539    0.071633     0.104533        0.0          1.432e-99  
 0.0135592    0.041803     0.0730543       0.0          2.01992e-14
 0.0          0.0138066    0.0426324       5.12635e-50  0.0        
 5.04373e-17  0.0          0.0140805    …  4.46428e-19  0.0        
 0.0          0.0          5.47168e-17     0.0          0.0        
 0.0          0.0          0.0             0.0          2.29313e-14
 4.47878e-6   1.41546e-17  5.76499e-17     2.53077e-14  1.94896e-34
 0.0256732    5.58846e-6   0.0             3.00369e-50  0.0        
 0.0511444    0.0259307    6.92451e-6   …  5.34525e-97  0.0        
 0.0716298    0.0516574    0.0262433       5.51751e-97  1.30167e-14
 0.0492006    0.0723464    0.0522801       0.0          2.21261e-34
 ⋮                                      ⋱                          
 3.32

### (b) Application to Synthetic Size Distributions

In [68]:
𝕟 = DMALognormalDistribution([[400, 30, 1.2],[500, 110, 1.7]], δ)

𝕣 = 𝐀[:,:]*𝕟                # Note 𝐀[:,:] = 𝐀, but changes the data type from Adjoint To Float64...
𝕟ⁱⁿᵛ = inv(𝐀)*𝕣 

# DMA response function 
figure("Arial", 2, 5, 2, 8)
p1 = plot(𝕟.Dp, 𝕟.S, xaxis = :log10, xticks = [10, 100, 1000], lt = :steppre, right_margin = 35px,
    legend = :none, ylabel = "dN/dlnD (cm⁻³)", xlim = (8,1000), color =  :black,
    xlabel = "Mobility Diameter (nm)",  label = "𝕟")

p1 = plot!(𝕟ⁱⁿᵛ.Dp, 𝕟ⁱⁿᵛ.S, color = :green, label = "𝕟ⁱⁿᵛ = 𝐀<sup>-1</sup>*𝕣")

p2 = plot(𝕣.Dp, 𝕣.N, label = "𝕣 = 𝐀*𝕟", xaxis = :log10, xticks = [10, 100, 1000], lt = :steppre, 
    right_margin = 35px,ylabel = "dN/dlnD (cm⁻³)", xlim = (8,1000), color =  :blue,
    xlabel = "Mobility Diameter (nm)")

plot(p1,p2, layout=grid(1,2))

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 15. </b> Forward and backward inversion of noise free data.

The next block creates a noisy response function based on counting statistics

In [69]:
𝕟 = DMALognormalDistribution([[400, 30, 1.2],[500, 110, 1.7]], δ)

Random.seed!(703)  # random number seed; fix for repeatable runs
tscan = 120        # SMPS scan time [s] 
Qcpc = 16.66       # CPC flow rate [cm³ s⁻¹]. 16.66 cm³ s⁻¹ = 1 L min⁻¹
t = tscan./bins    # time in each bin

𝕣 = δ.𝐀*𝕟;      # DMA response function 
c = 𝕣.N*Qcpc*t; # number of counts in each bin
R = Float64[]   # Construct a noisy response function 𝕣+ϵ, where ϵ is counting uncertainty
for i = c
    f = rand(Poisson(i),1)   # draw Poisson random number with mean = counts
    push!(R,f[1]/(Qcpc*t))   # convert back to concentration
end
R1 = R./𝕣.ΔlnD

𝕣 = SizeDistribution([],𝕣.De,𝕣.Dp,𝕣.ΔlnD,R./𝕣.ΔlnD,R,:respnse); # store as AerosolSizeDistribution

In [70]:
𝕟ᵢₙᵥ = inv(𝐀)*𝕣

figure("Arial", 2, 5, 2, 8)
p1 = plot(𝕟.Dp, 𝕟.S, xaxis = :log10, xticks = [10, 100, 1000], lt = :steppre, right_margin = 35px,
    legend = :none, ylabel = "dN/dlnD (cm⁻³)", xlim = (8,1000), color =  :black,
    xlabel = "Mobility Diameter (nm)",  label = "𝕟")

p1 = plot!(𝕟.Dp, 𝕟ᵢₙᵥ.S, color = :green, label = "𝕟ⁱⁿᵛ = 𝐀<sup>-1</sup>*𝕟")

p2 = plot(𝕣.Dp,𝕣.S, label = "𝕣 = 𝐀*𝕟", xaxis = :log10, xticks = [10, 100, 1000], lt = :steppre, 
    right_margin = 35px,ylabel = "dN/dlnD (cm⁻³)", xlim = (8,1000), color =  :blue,
    xlabel = "Mobility Diameter (nm)")

plot(p1,p2, layout=grid(1,2))

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 16. </b> Forward and backward inversion of noisy data.

#### Matrix 𝐀, 𝐒, 𝐈 

𝐈: Is the identity matrix
𝐀: Is the true convolution matrix, the small terms are the source of noise propagation
𝐒: A clever initial guess without noise: sum the rows of  𝐀  and placing the results on the diagonal of  𝐒 (Talukdar and Swihart, 2010)

In [71]:
T = (zˢ,k,Λ,δ) -> δ.Ω(Λ,δ.Z,zˢ/k).*δ.Tc(k,δ.Dp).*δ.Tl(Λ,δ.Dp)

𝐈 = Matrix{Float64}(I, bins, bins)
𝐒 = δ.𝐒
𝐀 = δ.𝐀
println(sum(𝐀[1,:]))
display("text/plain", 𝐈[1:5, 1:5])
display("text/plain", 𝐒[1:5, 1:5])
display("text/plain", 𝐀[1:5, 1:5])

5×5 Array{Float64,2}:
 1.0  0.0  0.0  0.0  0.0
 0.0  1.0  0.0  0.0  0.0
 0.0  0.0  1.0  0.0  0.0
 0.0  0.0  0.0  1.0  0.0
 0.0  0.0  0.0  0.0  1.0

5×5 Array{Float64,2}:
 0.204402  0.0       0.0       0.0       0.0     
 0.0       0.278665  0.0       0.0       0.0     
 0.0       0.0       0.325293  0.0       0.0     
 0.0       0.0       0.0       0.345664  0.0     
 0.0       0.0       0.0       0.0       0.353257

5×5 Array{Float64,2}:
 0.100718   0.0695514  0.0341323  4.43361e-10  0.0        
 0.0703494  0.102528   0.0709314  0.0348565    9.52379e-10
 0.0410539  0.071633   0.104533   0.0724363    0.0356367  
 0.0135592  0.041803   0.0730543  0.10672      0.0740579  
 0.0        0.0138066  0.0426324  0.0746043    0.109077   

0.20440176947549488


#### Talukdar and Swihart (2010) Approximate Solution
<center> $𝕟_{inv} = \bf{S}^{-1} \rm{𝕣}$ </center><br>

In [72]:
𝕟ᵢₙᵥ = inv(𝐒)*𝕣

figure("Arial", 2, 5, 2, 8)
p1 = plot(𝕟.Dp, 𝕟.S, xaxis = :log10, xticks = [10, 100, 1000], lt = :steppre, right_margin = 35px,
    legend = :none, ylabel = "dN/dlnD (cm⁻³)", xlim = (8,1000), color =  :black,
    xlabel = "Mobility Diameter (nm)",  label = "𝕟")

p1 = plot!(𝕟.Dp, 𝕟ᵢₙᵥ.S, color = :green, label = "𝕟ⁱⁿᵛ = 𝐀<sup>-1</sup>*𝕟")

p2 = plot(𝕣.Dp, 𝕣.S, label = "𝕣 = 𝐀*𝕟", xaxis = :log10, xticks = [10, 100, 1000], lt = :steppre, 
    right_margin = 35px,ylabel = "dN/dlnD (cm⁻³)", xlim = (8,1000), color =  :blue,
    xlabel = "Mobility Diameter (nm)")

plot(p1,p2, layout=grid(1,2))

<!DOCTYPE html>
 
 
 Plots.jl

#### Inversion using regularization

Apply regularized inversion with specified $\lambda$

<center> $𝕟_{inv} = \arg \min\{\left\rVert\bf{A}\rm{𝕟}-\rm{𝕣}\right\rVert_2^2 + \lambda^2 \left\rVert\rm{𝕟}-\bf{S}^{-1} \rm{𝕣}\right\rVert_2^2\}$ </center> <br>

<center> $𝕟_{inv} = (\bf{A}^\rm{T}\bf{A} + \lambda^\rm{2} \bf{I})^\rm{-1}(\bf{A}^\rm{T} \rm{𝕣} - \lambda^2\bf{S}^{-1} \rm{𝕣})$ </center><br>




In [73]:
λ = 0
𝕟ᵢₙᵥ = inv(𝐀'*𝐀 + λ^2.0*𝐈)*((𝐀'[:,:])*𝕣 + λ^2.0*(inv(𝐒)*𝕣))

@printf("Input number concentration %i\n", sum(𝕟.N))
@printf("Inverted number concentration %i\n", sum(𝕟ᵢₙᵥ.N))

figure("Arial", 2, 5, 2, 8)
p2 = plot(𝕟.Dp, 𝕟.S, xaxis = :log10, xticks = [10, 100, 1000],left_margin = 65px, ylabel = "dN/dlnD (cm⁻³)", 
    label = "𝕟 = 𝓛𝓝 (N,Dₘ,σ)", xlabel = "Mobility Diameter (nm)", xlim = (8,1000), ls = :dash, 
    lw = 2, color = :black)

p2 = plot!(𝕟ᵢₙᵥ.Dp, 𝕟ᵢₙᵥ.S, color = RGBA(0.8,0,0,1), lt = :steppre, 
    label = "N<sub>inv</sub>=(𝐀ᵀ𝐀+λ²𝐈)⁻¹(𝐀ᵀR-λ²𝐒⁻¹R)", xlim = (8,1000))#

p3 = plot(𝕣.Dp, R, xaxis = :log10, xticks = [10, 100, 1000], lt = :steppre,
    label = "𝕣 = 𝐀*𝕟+ϵ", ylabel = "Concentration (cm⁻³)", xlim = (8,1000),
    color = RGBA(0,0,0.8,1), xlabel = "Apparent +1 Mobility Diam. (nm)", left_margin = 65px)

plot(p2,p3, layout = (l = @layout [a b]), right_margin = 0px, legend=:right, 
    top_margin = 15px)

Input number concentration 900
Inverted number concentration 861


<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 17. </b> Inversion of noisy data with fixed λ. Change λ to evaluate...

In [74]:
λ₁,λ₂ = 1e-3, 1e1  # bounds [λ₁,λ₂] within which the optimal distribution lies

eyeM = Matrix{Float64}(I, bins, bins)
setupRegularization(δ.𝐀,eyeM,R,inv(δ.𝐒)*R)   # setup the system of equations to regularize
@time L1,L2,λs,ii = lcurve(λ₁,λ₂;n=200)      # compute the L-curve for plotting only
@time λopt = lcorner(λ₁,λ₂;n=10,r=3)         # compute the optimal λ using recursive algorithn
N =  clean((reginv(λopt, r = :Nλ))[1])       # find the inverted size distribution 
𝕟ᵢₙᵥ= SizeDistribution([],𝕟.De,𝕟.Dp,𝕟.ΔlnD,N./𝕟.ΔlnD,N,:regularized) # store as AerosolSizeDistribution

@printf("Input number concentration %i\n", sum(𝕟.N))
@printf("Inverted number concentration %i\n", sum(𝕟ᵢₙᵥ.N))

figure("Arial", 2, 6, 4.5, 10)

p1 = plot(L1, L2, xaxis = :log10, yaxis = :log10, xlabel = "||𝐀*𝕟-𝕣||", ylabel = "||𝕟-𝐒<sup>-1</sup>𝕣||", color = :black, 
    label = "L-curve"*(@sprintf(" λ ∈ [%.0e %.0e]", λ₁,λ₂)), bottom_margin = 50px)

p1 = plot!([L1[ii], L1[ii]], [L2[ii], L2[ii]], marker = :square, color = RGBA(0.8,0,0,0.5), 
            label = "Optimum λ ="*(@sprintf("%.1e", λopt)),lw = 0, ms = 4)

p2 = plot(𝕟.Dp, 𝕟.S, xaxis = :log10, xticks = [10, 100, 1000],left_margin = 65px, ylabel = "dN/dlnD (cm⁻³)", 
    label = "𝕟 = 𝓛𝓝 (N,Dₘ,σ)", xlabel = "Mobility Diameter (nm)", xlim = (8,1000), ls = :dash, 
    lw = 3, color = :black)

p2 = plot!(𝕟ᵢₙᵥ.Dp, 𝕟ᵢₙᵥ.S, color = RGBA(0.8,0,0,1), lt = :steppre, 
    label = "N<sub>inv</sub>=(𝐀ᵀ𝐀+λ²𝐈)⁻¹(𝐀ᵀR-λ²𝐒⁻¹R)", xlim = (8,1000))

p3 = plot(𝕣.Dp, R, xaxis = :log10, xticks = [10, 100, 1000], lt = :steppre,
    label = "𝕣 = 𝐀*𝕟+ϵ", ylabel = "Concentration (cm⁻³)", xlim = (8,1000),
    color = RGBA(0,0,0.8,1), xlabel = "Apparent +1 Mobility Diam. (nm)", left_margin = 65px)

plot(p1,p2,p3, layout = (l = @layout [a; b c]), right_margin = 0px, legend=:right, 
    top_margin = 15px)

  9.232731 seconds (151.66 k allocations: 1.689 GiB, 3.28% gc time)
  1.141556 seconds (30.43 k allocations: 345.851 MiB, 5.14% gc time)
Input number concentration 900
Inverted number concentration 892


<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 18.</b> Top: L-curve of $L_1$ vs. $L_2$. The L-curve is computed from the interval [λ₁,λ₂] using the lcurve() function. The optimum $\lambda_{opt}$ is determined from the interative algorithm lcorner(). Bottom left: dashed line is the input size distribution (as in Figure 1). Red line is the regularized inverse of the noisy response function shown in the bottom right (as in Figure 2). 

### (c) Inversion of Real Data

Sheath flow = 4 L min-1 and sample aerosol flow = 1 L min-1 and specified in the data file.

<b> loadtsidata </b> Loads txt file exported from TSI Aerosol Instrument Manager (20130618_1410_SMPS3_BP.txt). The file was edited to remove a unicode character in line 154 that results in a load error. The load function will need to be adapted for files with different scan length and export parameters. The data corresponds to ambient data collected by Dr. Grieshop and Saha during the SOAS campaign (Saha et al., 2017). It contains a total of 160 spectra. The instrument was operated at 4 L min-1 sheath flow and 1 L min-1 sample flow with a TSI 3081 long column DMA and TSI 3010 CPC. The data were exported with multiple charge correction turned on and diffusion correction turned off.  <br>
𝕟: Array of TSI inverted size distribution <br>
rawdp: raw diameter grid obtained at 10Hz acquisition <br>
rawc: 2D array containing raw counts vs diameter for each spectrum <br>
Nt_TSI: array of integrated number concentration computed by TSI software

In [75]:
t,p = 295.15, 1e5                                # Temperature [K], Pressure [Pa]
qsa,β = 1.66e-5, 1/4                             # Qsample [m3 s-1], Sample-to-sheath ratio,
r₁,r₂,l = 9.37e-3,1.961e-2,0.44369               # DMA geometry [m]
leff = 0.0                                       # DMA effective diffusion length [m]
m = 6                                            # Upper number of charges
Λ = DMAconfig(t,p,qsa,qsa/β,r₁,r₂,l,leff,:-,m,:cylindrical) # Specify DMA with negative polarity
tscan, tc = 120,1                                # SMPS scan time, bin average time
v1,v2 = 10,10000                                 # Voltage range
z1,z2 = vtoz(Λ,v2), vtoz(Λ,v1)
δ = setupSMPS(Λ, v1, v2, tscan, tc);
𝕟, rawdp, rawc, Nt_TSI = loadtsidata();

The response function is computed from the 10 Hz raw count data. The raw counts falling within a bin are summed together. Concentration is computed from the number of milliseconds in each bin. The coincidence corrected concentration is obtained using Eq. (11) in Collins et al. (2003) <br><br>

<center> $N_a = \frac{-W(-N_m Q_{cpc}\tau)}{Q_{cpc}\tau}$ </center> 

where $N_a$ is the coincidence corrected concentration, $N_m$ is the measured raw concentration, $Q_{cpc}$ is the volumetric CPC flow rate, $\tau$ is the beam transit time, and $W$ is the zero branch of the LambertW function. Here $\tau = 0.4\mu s$, where the value is for the TSI 3010 CPC and obtained from the manufacturer manual.

In [76]:
Qcpc,τ = 16.6666, 0.4e-6   # 1 L min-1 = 16.6666 cm3 s-1, 0.4 μs 
correct = @. x -> -lambertw(-x*Qcpc*τ,0)/(Qcpc*τ)

a,b = size(rawc)
𝕣 = SizeDistribution[]
for j = 1:b
    R = Float64[]
    for i = 1:length(δ.De)-1
        ii = (rawdp .<= δ.De[i]) .& (rawdp .> δ.De[i+1])
        un = rawdp[ii]
        c = rawc[ii,j]
        Nm = length(c) > 0 ? sum(c)./(length(c)*1.6666) : 0
        Na = correct(Nm)
        push!(R,Na)
    end
    push!(𝕣, SizeDistribution([],δ.De,δ.Dp,δ.ΔlnD,R./δ.ΔlnD,R,:raw))
end

j = 110  # plot example distribtution
figure("Arial", 2, 3, 2, 8)
p = plot(𝕣[j].Dp, 𝕣[j].N,xaxis = :log10,xticks = [10, 100, 1000],lt = :steppre,legend = :none,color = :black,
    ylabel = "Concentration (cm⁻³)", xlim = (8,1000), xlabel = "Apparent +1 Mobility Diam. (nm)", 
    right_margin = 25px)

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 19. </b> Coincidence corrected raw response function obtained from raw counts.

The block makes use of the wrapper function rinv(), which computes the inverse of a response function and returns a size distribution. It is the same code as applied above to the synthetic data.
```julia
function rinv(R, δ;λ₁= 1e-2, λ₂=1e1)
    eyeM = Matrix{Float64}(I, length(R), length(R))
    setupRegularization(δ.𝐀,eyeM,R,inv(δ.𝐒)*R) # setup the system
    λopt = lcorner(λ₁,λ₂;n=10,r=3)                  # compute the optimal λ
    N =  clean((reginv(λopt, r = :Nλ))[1])          # find the inverted size
    return SizeDistribution([],δ.De,δ.Dp,δ.ΔlnD,N./δ.ΔlnD,N,:regularized)
end
```

In [77]:
λ₁,λ₂ = 1e-2, 1e1  # bounds [λ₁,λ₂] within which the optimal distribution lies

@time 𝕟ᵢₙᵥ = rinv(𝕣[j].N, δ,λ₁=λ₁,λ₂=λ₂);

figure("Arial", 2, 5.75, 1.75, 8)

p2 = plot(𝕟ᵢₙᵥ.Dp, 𝕟ᵢₙᵥ.S, xaxis = :log10, xticks = [10, 100, 1000],
    ylabel = "dN/dlnD (cm⁻³)", label = "TSI AIM Inversion", xlim = (8,1000),  
    color = :black, xlabel = "Mobility Diameter (nm)", left_margin = 30px, lw= 1.5)

p2 = plot!(𝕟ᵢₙᵥ.Dp, 𝕟ᵢₙᵥ.S, color = RGBA(163/255,0,0,1),
    lt = :steppre, label = "N=(𝐀ᵀ𝐀+λ²𝐈)⁻¹(𝐀ᵀR-λ²𝐒⁻¹R)", xlim = (8,1000))

p3 = plot(𝕣[j].Dp, 𝕣[j].N, xaxis = :log10, xticks = [10, 100, 1000], lt = :steppre,
    label = "R measured", ylabel = "Concentration (cm⁻³)", xlim = (8,1000),left_margin = 30px,
    color = RGBA(58/255,129/255,252/255,1), xlabel = "Apparent +1 Mobility Diam. (nm)")

plot(p2,p3, layout = grid(1,2), right_margin = 30px, top_margin = 0px)

  0.924606 seconds (30.47 k allocations: 346.582 MiB, 7.14% gc time)


<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 20. </b> Left: Size distribution expressed as dN/dlnD output by TSI AIM software and the inversion performed in Block 3. Right: Measured response function as shown in Figure 19.

# 5. Size-resolved CCN Measurements

Size resolved CCN measurements have a long history (e.g. Cruz and Pandis, 1997, Snider et al., 2006). The basic configuration is shown in Figure 21. Particles are typically dried, charge neutralized, and passed through the DMA. At the exit, the flow is split between a CPC that measures all particles and a CCN counter that measures particles that form cloud droplets at a water supersaturation set by the instrument. In this configuration the DMA voltage can either be stepped or continuously scanned. The ratio of CCN-to-CPC response function is used to determine the fraction of particles that activate at a given diameter. The diameter where 50% of the particles activate is taken to be the activation diameter. <br>

<img src="Figures/nbs7_f01.png" width="350">
<figcaption><b> Figure 21. </b> Schematic of instrument setup for size resolved CCN measurements.  </figcaption> 

The activation of particles into cloud droplets is proportional to the volume of solute in the particle. Therefore, larger multiply charged particles activate first. This leads to a bias in the inferred D50 diameter if the activated fraction is computed from the ratio of the raw response functions (Petters et al., 2007, 2009).

In [78]:
t,p = 295.15, 1e5                                # Temperature [K], Pressure [Pa]
qsa,β = 1.66e-5, 1/10                            # Qsample [m3 s-1], Sample-to-sheath ratio,
r₁,r₂,l = 9.37e-3,1.961e-2,0.44369               # DMA geometry [m]
leff = 13.0                                      # DMA effective diffusion length [m]
m = 6                                            # Upper number of charges
Λ = DMAconfig(t,p,qsa,qsa/β,r₁,r₂,l,leff,:-,m,:cylindrical)   # Specify DMA with negative polarity
bins,z₁,z₂ = 256, dtoz(Λ,1000e-9), dtoz(Λ,10e-9) # bins, upper, lower mobility limit
δ = setupDMA(Λ, z₁, z₂, bins);                   # Compute matrices

## (a) Introduction

The CCN transmission function is modelded using a cumulative Gauss integral <br>
<center> $T_{af} = \frac{1}{2}\left[1 + \mathrm{erf}\left(\frac{d-\mu}{\sigma}\right) \right] $ </center>
This function is applied to the mobility size distribution. Then the response function is computed. Empirically, activated fraction can be computed using from the ratio of size distributions and response functions. 

In [79]:
# CCN efficiency function 
#  - 𝕟 is a size distribution from which the diameter vector is used
#  - μ is the activation diameter
#  - σ is the spread
Taf = (𝕟,μ,σ) -> 0.5 .* (1.0 .+ erf.((𝕟.Dp .- μ)./(sqrt(2σ))))
μ,σ = 60,8

# Generate a lognormal size distribution that serves as input. 
# The size distribution is computed on the DMA size grid defined by DMA δ1 and δ2
#   - Nt is in [# m-3] for calculations with k12
#   - Dg is in nm in accordance with the grid uings
#   - σ is the geometeric standard deviation (σ > 1)
# Multiple modes can be defined by concatenation. A single mode is permissible A = [[Nt1,Dg1,σ1]]
𝕟ᶜⁿ = DMALognormalDistribution([[1800, 80, 1.4]], δ)
𝕟ᶜᶜⁿ = Taf(𝕟ᶜⁿ,μ,σ)*𝕟ᶜⁿ  # CCN distribution function
𝕣ᶜⁿ = δ.𝐀*𝕟ᶜⁿ               # CN response function. δ.A is the forward matrix for DMA δ
𝕣ᶜᶜⁿ = δ.𝐀*𝕟ᶜᶜⁿ             # CCN response function. δ.A is the forward matrix for DMA δ  
𝕒𝕗₁ =  𝕟ᶜᶜⁿ/𝕟ᶜⁿ            # ratio of CCN to CN based on real size distribution. This recovers g
𝕒𝕗₂ =  𝕣ᶜᶜⁿ/𝕣ᶜⁿ;           # ratio of CCN to CN based on response function (measured)

In [80]:
figure("Arial", 2, 5.5, 3.5, 8)  

# Get a list of colors from the theme palette
p = Plots.get_color_palette(:auto, default(:bgcolor), 100)

# Panel (a): Mobility size and CCN distribution
p1 = plot(𝕟ᶜⁿ.Dp, 𝕟ᶜⁿ.S, xaxis = :log10, xticks = [10, 100, 1000], ylabel = "dN/dlnD (cm⁻³)", 
    label = "𝕟ᶜⁿ = 𝓛𝓝 (N,Dₘ,σ)", color = p[1],  left_margin = 20px)
p1 = plot!(𝕟ᶜᶜⁿ.Dp, 𝕟ᶜᶜⁿ.S, label = "𝕟ᶜᶜⁿ = Taf.*𝕟ᶜⁿ", color = p[2])

# Panel (b): Size and CCN response function 
p2 = plot(𝕣ᶜⁿ.Dp, 𝕣ᶜⁿ.N , xaxis = :log10, xticks = [10, 100, 1000], label = "𝕣ᶜⁿ = 𝐀*𝕟ᶜⁿ", 
    ylabel = "Concentration (cm⁻³)", color = p[3])
p2 = plot!(𝕣ᶜᶜⁿ.Dp, 𝕣ᶜᶜⁿ.N, label = "𝕣ᶜᶜⁿ = 𝐀*𝕟ᶜᶜⁿ", color = p[4], left_margin = 36px)

# Panel (c): Activated fraction. Note that g and 𝕒𝕗₁ are identical
p3 = plot(𝕒𝕗₁.Dp, 𝕒𝕗₁.S, xaxis = :log10, xticks = [10, 100, 1000], xlabel = "Mobility Diameter (nm)", 
    ylabel = "Activated fraction", label = "𝕟ᶜᶜⁿ ./ 𝕟ᶜⁿ", ylim = (-0.05,1.05), lw = 1.5, 
    yticks = [0, 0.2, 0.4, 0.6, 0.8, 1], color = :black,  left_margin = 20px)
p3 = plot!(𝕟ᶜⁿ.Dp, Taf(𝕟ᶜⁿ,μ,σ), label = "Taf = ½[1+erf((Dₚ-μ)/(√2σ)]", ls = :dash, 
    color = :darkorange, lw = 1.5)

# Panel (d): Activated fraction from response function ("measured ratio" from raw signal)
p4 = plot(𝕒𝕗₂.Dp, 𝕒𝕗₂.S, xaxis = :log10, xticks = [10, 100, 1000],  
    xlabel = "Apparent +1 Mobility Diam. (nm)", ylim = (-0.05,1.05), label = "𝕣ᶜᶜⁿ ./ 𝕣ᶜⁿ", 
    color = p[7], ylabel = "Activated fraction", yticks = [0, 0.2, 0.4, 0.6, 0.8, 1], left_margin = 20px)

plot(p1,p2,p3,p4, layout = grid(2,2), lw = 1.5, right_margin = 30px, 
    xlim = (20,200), legend=:right, top_margin = 15px)

<!DOCTYPE html>
 
 
 Plots.jl

<figcaption><b> Figure 22. </b> Top left: Lognormal mobility size distribution (CN) assumed to be known (blue) and CCN size distribution calculated from the assumed size distribution and the CCN transmission function based on an assumed D50 activation diameter of (μ=60 nm) and standard deviation (σ = 8nm). Top right: CN and CCN response funcion computed from size and CCN distribution and the convolution matrix. Bottom left: ratio of  CCN and CN size distribution superimposed on the CCN transmission function. These are by definition equal. Bottom right, right of CCN and CN response function. </figcaption> 

Figure 22 bottom right demostrates the presence of a shoulder of particles activating at 45 nm. These are +2 charged particles transmitting through the DMA that influence of +2 the observed ratio 𝕣ᶜᶜⁿ./𝕣ᶜⁿ. Petters et al. (2007) used a non-matrix based forward solution of the Fredholm integral equation to compute 𝕣ᶜᶜⁿ./𝕣ᶜⁿ and fit an optimal solution through data. Petters et al. (2009) used an simple inversion method to find 𝕟ᶜᶜⁿ./𝕟ᶜⁿ, from which the activated fraction and D50 were determined. Neither method is quick to reproduce. 


## (b) Application to Synthetic  Data

Here the objective is to find the activation diameter when only the noisy response is known, as is the case with measurements. A noisy response function is simulated as in Notebook S4. The ideal response function is computed via 𝕣 = $\mathbf{A}*$𝕟. Then the number of counts are computed based on detector sample flow rate (1 L min⁻¹ for the CPC and 0.05 L min⁻¹ for the CCN). A random number generator is simulating a Poisson distributed random variate with mean equaling the counts. The noisy response function is thresholded at low concentrations. This is necessary because at low concentrations a bin may have zero or very low concentration, resulting in unrealistic or NaN/InF values in the activated fraction array. The data are then inverted and the activation diameter is obtained via a non-linear least square fit, as would be the case with a real dataset.

In [81]:
t,p = 295.15, 1e5                                # Temperature [K], Pressure [Pa]
qsa,β = 1.66e-5, 1/5                             # Qsample [m3 s-1], Sample-to-sheath ratio,
r₁,r₂,l = 9.37e-3,1.961e-2,0.44369               # DMA geometry [m]
leff = 13.0                                      # DMA effective diffusion length [m]
m = 6                                            # Upper number of charges
Λ = DMAconfig(t,p,qsa,qsa/β,r₁,r₂,l,leff,:-,m,:cylindrical)   # Specify DMA with negative polarity
bins,z₁,z₂ = 60, dtoz(Λ,300e-9), dtoz(Λ,30e-9)   # bins, upper, lower mobility limit
δ = setupDMA(Λ, z₁, z₂, bins);                   # Compute matrices

The section generates the noisy CN and CCN response function using the random number gnerator. Thresholding is performed for bins with low counts. If counts/concentration is below the threhold, the activated fraction is forced to one for large diameters and zero for small diameters. The noise threshold may need to be adjusted for different datasets.

In [82]:
𝕟ᶜⁿ = DMALognormalDistribution([[7000.0, 80, 1.3]], δ)
Taf = (x,μ,σ) -> @. 0.5 .* (1.0 .+ erf.((x .- μ)/(sqrt(2σ))))
tscan = 180        # SMPS scan time [s] 
Qcpc = 16.66       # CPC flow rate [cm³ s⁻¹]. 16.66 cm³ s⁻¹ = 1 L min⁻¹
Qccn = 0.05*16.66  # CCN sample flow rate [cm³ s⁻¹]. 16.66 cm³ s⁻¹ = 1 L min⁻¹
t = tscan./bins    # time in each bin
Random.seed!(705)
μ,σ = 60,8
𝕣ᶜⁿ = δ.𝐀*𝕟ᶜⁿ;                     # DMA response function 
𝕣ᶜᶜⁿ = δ.𝐀*(Taf(δ.Dp,μ,σ)*𝕟ᶜⁿ);   # DMA response function 
cᶜⁿ = 𝕣ᶜⁿ.N*Qcpc*t;                # number of counts in each bin
cᶜᶜⁿ = 𝕣ᶜᶜⁿ.N*Qccn*t;              # number of CCN counts in each bin

Rcn = Float64[]    # Construct a noisy response function 𝕣+ϵ, where ϵ is counting uncertainty
Rccn = Float64[]   # Construct a noisy response function 𝕣+ϵ, where ϵ is counting uncertainty
for i = cᶜⁿ
    f = rand(Poisson(i),1)     # draw Poisson random number with mean = counts
    push!(Rcn,f[1]/(Qcpc*t))   # convert back to concentration
end

for i = cᶜᶜⁿ
    f = rand(Poisson(i),1)      # draw Poisson random number with mean = counts
    push!(Rccn,f[1]/(Qccn*t))   # convert back to concentration
end

𝕣ᶜⁿ.N, 𝕣ᶜᶜⁿ.N  = Rcn, Rccn;

function threshold(𝕟::SizeDistribution, c::Float64, n1::Float64, n2::Float64)
   N = 𝕟.N  
   N[(N .<= c) .& (𝕟.Dp .> 150)] .= n1
   N[(N .<= c) .& (𝕟.Dp .> 150)] .= n2
   𝕟.N = N
end

threshold(𝕣ᶜⁿ, 6.0, 0.1, 0.1);
threshold(𝕣ᶜᶜⁿ, 6.0, 0.0, 0.1);

The data are inverted using the regularized inversion (Notebook S4). The regularized inverted size distributions are are also thresholded for the same reason as above. Zero concentrations in the CN array or division of two noisy numbers results in unrealistic activated fractions that interfere with the least-square fitting model. <br>

### Fitting Model
There are two ways to fit the response data. Possibility one is to compute the activated fraction from the inverted data and then fit the ratio to the activation model
<center> $T_{\mu,\sigma} = \frac{1}{2}\left[1 + \mathrm{erf}\left(\frac{d-\mu}{\sigma}\right) \right] $ </center>
to find the μ,σ that best describes the data. An alternative method is to compute the regularized inverse from the the CN response function and use it to predict the ratio of 𝕣ᶜⁿ./𝕣ᶜᶜⁿ. In this case the model is
<center> $𝕟^{\mathrm{cn}} = (\bf{A}^\rm{T}\bf{A} + \lambda^\rm{2} \bf{I})^\rm{-1}(\bf{A}^\rm{T} \rm{𝕣^{\mathrm{cn}}} - \lambda^2\bf{S}^{-1} \rm{𝕣^{\mathrm{cn}}})$ </center>
<center> $\left( \frac{𝕣^{\mathrm{cn}}}{𝕣^{\mathrm{cn}}} \right)_{\mathrm{model}} = \frac{\mathbf{A}[T_{\mu,\sigma}\; .*\; 𝕟^{\mathrm{cn}}]}{\mathbf{A}𝕟^{\mathrm{cn}}}$ </center>
Methods 1 and 2 mirror the approaches in Petters et al. (2009) and Petters et al. (2007), respectively. However, the previously published approaches neither used regularization nor the formalism described here. <br>

Using the formalized approach, the model formulation and fitting procedure become simple and can be solved in few lines of code.
```julia
𝕟ᶜⁿ = rinv(𝕣ᶜⁿ.N, δ, λ₁= 1e-3, λ₂=1e1)
model(x,p) = (δ.𝐀*(𝕟ᶜⁿ.N.*Taf(δ.dp, p[1], p[2])))./(δ.𝐀*𝕟ᶜⁿ.N)
fit = curve_fit(model, δ.Dp, 𝕣ᶜᶜⁿ.N./𝕣ᶜⁿ.N, [65.0, 3.0])
```
Note that least square library is not setup to take the SizeDistribution data type, and thus the operation is performed on the number field of these objects. 

In [83]:
𝕟ᶜⁿ = rinv(𝕣ᶜⁿ.N, δ, λ₁= 1e-3, λ₂=1e1)
𝕟ᶜᶜⁿ = rinv(𝕣ᶜᶜⁿ.N, δ, λ₁= 1e-3, λ₂=1e1)
threshold(𝕟ᶜⁿ, 60.0, 0.1, 0.1)
threshold(𝕟ᶜᶜⁿ, 60.0, 0.0, 0.1)
𝕒𝕗₁ =  𝕟ᶜᶜⁿ/𝕟ᶜⁿ           # ratio of CCN to CN based on inverted data

model(x,p) = (δ.𝐀*(𝕟ᶜⁿ.N.*Taf(δ.Dp, p[1], p[2])))./(δ.𝐀*𝕟ᶜⁿ.N)
fit = curve_fit(model, δ.Dp, 𝕣ᶜᶜⁿ.N./𝕣ᶜⁿ.N, [65.0, 3.0])
Ax = fit.param;
DataFrame(μ=round(Ax[1],digits=1), σ=round(Ax[2],digits=1))

1×2 DataFrame
│ Row │ μ       │ σ       │
│     │ Float64 │ Float64 │
├─────┼─────────┼─────────┤
│ 1   │ 59.6    │ 8.7     │

In [84]:
figure("Arial", 2, 5.5, 3, 8)
pre = 1e-3

p1 = plot(δ.Dp, 𝕣ᶜⁿ.N, xaxis = :log10, xticks = [10, 100, 1000], ylabel = "Concentration (cm⁻³)", 
    label = "𝕣ᶜⁿ",  color = :black, lt = :steppre)
p1 = plot!(δ.Dp, 𝕣ᶜᶜⁿ.N, label = "𝕣ᶜᶜⁿ", color = RGBA(163/255,0,0,1), lt = :steppre,
        left_margin = 40px)

p2 = plot(𝕟ᶜⁿ.Dp, pre.*𝕟ᶜⁿ.S, xaxis = :log10, xticks = [10, 100, 1000], 
     ylabel = "dN/dlnD × 10⁻³ (cm⁻³)",  label = "𝕟ᶜⁿ (Eq. 10)", color = :black, 
     ls = :dashdot, lt = :steppre)
p2 = plot!(𝕟ᶜᶜⁿ.Dp, pre.*𝕟ᶜᶜⁿ.S, label = "𝕟ᶜᶜⁿ (Eq. 10)", color = RGBA(163/255,0,0,1), 
    ls = :dashdot, lt = :steppre, left_margin = 52px)

p3 = scatter(δ.Dp, 𝕣ᶜᶜⁿ.N./𝕣ᶜⁿ.N, xaxis = :log10, xticks = [10, 100],  
    xlabel = "Apparent +1 Mobility Diameter (nm)", ms = 3, 
    ylabel = "Activated fraction", ylim = (-0.05,1.25), label = "𝕣ᶜᶜⁿ./𝕣ᶜⁿ", markercolor = :darkorange,
     left_margin = 30px)

p3 = plot!(δ.Dp, model(δ.Dp, Ax), label = "Eq. (12)", color = :black , lw = 2, left_margin = 65px)

p4 = scatter(𝕒𝕗₁.Dp, 𝕒𝕗₁.N, xaxis = :log10, xticks = [10, 100, 1000], ms = 3,
    xlabel = "Mobility Diameter (nm)", ylabel = "Activated fraction", label = "𝕟ᶜᶜⁿ/𝕟ᶜⁿ", 
    markercolor = :white, ylim = (-0.05,1.25), left_margin = 25px)

p4 = plot!(δ.Dp, Taf(δ.Dp,Ax[1],Ax[2]), label = "Eq. (11)", color = :black, lw = 2, ls = :dashdot)

plot(p1,p2,p4,p3, layout = grid(2,2),  bottom_margin = 10px, xlim =(30,130), 
    legend = :topright, lw = 2, right_margin = 2px)

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 23. </b> Top left: Synthetic noisy response functions for CN and CCN instruments. Note that the CCN response function is more noisy due to the smaller sample flow rate. Top right: inverted CN and CCN size distribution. Bottom left: circles are the ratio of CCN and CN response functions from the synthetic data. The solid line corresponds to the model with the parameters returned from the least-square fit. Bottom right: circles are the ratio of CCN and CN concentration from the regualurized inverse of the response function. The line corresponds the activation model using the parameters returned from the least-square fit. Note that for D > ~200 nm the activated fraction is set to unity and for D < ~35 nm is set to zero by threholding applied. Further note that the inversion removes the shoulder to the left of the true activation diameter, as is expected. Finally, note that the activated fraction is more noisy in the bottom right plot relative to the bottom left plot. 

# 6. Tandem DMA

The tandem DMA has first been described by Rader and McMurry (1986). Tandem DMA measurements are highly versatile. Park et al. (2008) reviewed an impressive list of different combinations of DMAs and detectors that have been used. Since then, additional measurement setups have been introduced in the literature. Figure 24 summarizes a typical hygroscopicity tandem DMA setup (HTMDA). Dried, charge equilibrated particles are classified in DMA 1. The flow is split to measure particle concentration with a condensation particle counter (CPC). The remaining flow is passed through a humidifier. Hygroscopic particles take up water and increase in diameter. The humidified size distribution is measured using the second DMA that is operated in scanning or stepping mode. Passage through a second bipolar charger (charge neutralizer) is optional and rarely used in TDMA experiments.  <br>

<img src="Figures/nbs8_f01.png" width="700">
<figcaption><b> Figure 24. </b> Schematic of a typical HTDMA setup. D </figcaption> 

## (a) Hygroscopicity TDMA

In [85]:
t,p = 295.15, 1e5                                # Temperature [K], Pressure [Pa]
qsa,β = 1.66e-5, 1/5                             # Qsample [m3 s-1], Sample-to-sheath ratio,
r₁,r₂,l = 9.37e-3,1.961e-2,0.44369               # DMA geometry [m]
leff = 13.0                                      # DMA effective diffusion length [m]
m = 3                                            # Upper number of charges
Λ₁ = DMAconfig(t,p,qsa,qsa/β,r₁,r₂,l,leff,:-,m,:cylindrical)  # Specify DMA with negative polarity
Λ₂ = DMAconfig(t,p,qsa,qsa/β,r₁,r₂,l,leff,:+,m,:cylindrical)  # Specify DMA with negative polarity
bins,z₁,z₂ = 512, dtoz(Λ₁,500e-9),dtoz(Λ₁,30e-9) # bins, upper, lower mobility limit
δ₁ = setupDMA(Λ₁, z₁, z₂, bins);                 # Compute matrices
δ₂ = setupDMA(Λ₂, z₁, z₂, bins);                 # Compute matrices

In [86]:
Dm = 100.0                      # Size select 100 nm mobility diameter
gf = 2.0                        # Assumed diameter growth factor
zˢ = dtoz(Λ₁, Dm*1e-9);         # Compute corresponding electrical mobility
T = (zˢ,k,Λ,δ) -> δ.Ω(Λ,δ.Z,zˢ/k).*δ.Tc(k,δ.Dp).*δ.Tl(Λ,δ.Dp);  # DMA Transmission (Notebook 2,4)

Ax = [[1300., 60., 1.4], [2000., 200., 1.6]]   
𝕟ᶜⁿ = DMALognormalDistribution(Ax, δ₁)        # Assumed lognormal size distribution
𝕣ᶜⁿ = δ₁.𝐀*𝕟ᶜⁿ                                # CN response function. δ1.A is the forward matrix for DMA δ1

𝕟 = map(k->T(zˢ,k,Λ₁,δ₁)*𝕟ᶜⁿ,1:Λ₁.m)         # 𝕟[k] : Real size distribution of +k charges (neg. pol. DMA)
𝕘 = map(k->gf⋅(T(zˢ,k,Λ₁,δ₁)*𝕟ᶜⁿ),1:Λ₁.m)    # 𝕘[k] : Real size distributions shifted by growth factor gf 
𝕩 = map(k->(ztod(Λ₁,1,zˢ)/ztod(Λ₁,k,zˢ))⋅(T(zˢ,k,Λ₁,δ₁)*𝕟ᶜⁿ),1:Λ₁.m)      # Mobility size dist +k charges
𝕪 = map(k->(ztod(Λ₁,1,zˢ)/ztod(Λ₁,k,zˢ))⋅(gf⋅(T(zˢ,k,Λ₁,δ₁)*𝕟ᶜⁿ)),1:Λ₁.m) # Mobility size shifted by gf  

𝕟ₜ,𝕘ₜ,𝕩ₜ,𝕪ₜ = sum(𝕟),sum(𝕘),sum(𝕩),sum(𝕪); # 𝕟ₜ,𝕘ₜ,𝕩ₜ,𝕪ₜ : Reconstructed total size distribution 
𝕤𝕘,𝕤𝕘ₜ,𝕤𝕪 = map(k->δ₂.𝐀*𝕘[k], 1:3),δ₂.𝐀*𝕘ₜ,δ₂.𝐎*𝕪ₜ; # Distribution after passage through the second DMA

In [87]:
figure("Arial", 2, 6.5, 5, 8)

# Get a list of colors from the theme palette
p = Plots.get_color_palette(:auto, default(:bgcolor), 100)

p1 = plot(𝕟ᶜⁿ.Dp, 𝕟ᶜⁿ.S, xaxis = :log10, xticks = [10, 100, 1000], ylabel = "dN/dlnD (cm⁻³)", 
    label = "𝕟ᶜⁿ = 𝓛𝓝 (N,Dₘ,σ)", color = :black, left_margin = 15px)

p2 = plot(𝕣ᶜⁿ.Dp, 𝕣ᶜⁿ.N, xaxis = :log10, xticks = [10, 100, 1000], 
    label = "𝕣ᶜⁿ = 𝐀*𝕟ᶜⁿ", ylabel = "Conc. (cm⁻³)", color = RGBA(0.8,0,0), ylim = (0,62), left_margin = 15px)

p3 = plot(𝕩[1].Dp,𝕩[1].S, xaxis = :log10, xlim = (50,500), label = "𝕞₁ = f₁⋅𝕟₁", 
    ylabel = "dN/dlnD (cm⁻³)")
p3 = plot!(𝕩[2].Dp,𝕩[2].S, label = "𝕞₂ = f₂⋅𝕟₂")   
p3 = plot!(𝕩[3].Dp,𝕩[3].S, label = "𝕞₃ = f₃⋅𝕟₃")   
p3 = plot!(𝕩ₜ.Dp,𝕩ₜ.S, ls = :dashdot, color = :black, label = "𝕞ₜ = ∑(fᵢ*𝕟₁)")   

p4 = plot(𝕟[1].Dp,𝕟[1].S, xaxis = :log10, xlim = (50,500), label = "𝕟₁ = T₁*𝕟ᶜⁿ", 
    ylabel = "dN/dlnD (cm⁻³)")
p4 = plot!(𝕟[2].Dp,𝕟[2].S, label = "𝕟₂ = T₂*𝕟ᶜⁿ")   
p4 = plot!(𝕟[3].Dp,𝕟[3].S, label = "𝕟₃ = T₃*𝕟ᶜⁿ")   
p4 = plot!(𝕟ₜ.Dp,𝕟ₜ.S, ls = :dashdot, color = :black, label = "𝕟ₜ = ∑(Tᵢ * 𝕟ᶜⁿ)")   

p5 = plot(𝕪[1].Dp,𝕪[1].S, xaxis = :log10, xlim = (50,500), label = "gf⋅𝕞₁", 
    ylabel = "dN/dlnD (cm⁻³)")
p5 = plot!(𝕪[2].Dp,𝕪[2].S, label = "gf⋅𝕞₂")   
p5 = plot!(𝕪[3].Dp,𝕪[3].S, label = "gf⋅𝕞₃")   
p5 = plot!(𝕪ₜ.Dp,𝕪ₜ.S, ls = :dashdot, color = :black, label = "∑(gf⋅𝕞ᵢ)")   

p6 = plot(𝕘[1].Dp,𝕘[1].S, xaxis = :log10, xlim = (50,500), label = "gf⋅(T₁*𝕟ᶜⁿ)", 
    ylabel = "dN/dlnD (cm⁻³)")
p6 = plot!(𝕘[2].Dp,𝕘[2].S, label = "gf⋅(T₂*𝕟ᶜⁿ)")   
p6 = plot!(𝕘[3].Dp,𝕘[3].S, label = "gf⋅(T₃*𝕟ᶜⁿ)")   
p6 = plot!(𝕘ₜ.Dp,𝕘ₜ.S, ls = :dashdot, color = :black, label = "∑(gf⋅(Tᵢ*𝕟ᶜⁿ))")   

p7 = plot(𝕤𝕪.Dp,𝕤𝕪.N, color = :black, ls = :dashdot, label = "O*∑(gf⋅𝕞ᵢ)", ylim = (0,25),
    ylabel = "Conc. (cm⁻³)", xlabel = "Diameter (nm)", xscale = :log10, xlim = (50,500))

p8 = plot(𝕤𝕘[1].Dp,𝕤𝕘[1].N, xaxis = :log10, xlim = (50, 500), xlabel = "Diameter (nm)",  ylim = (0,5.5),
    ylabel = "Conc. (cm⁻³)", label = "𝕤₁ = 𝐀₂*(gf⋅(T₁*𝕟ᶜⁿ))")   
p8 = plot!(𝕤𝕘[2].Dp,𝕤𝕘[2].N,  label = "𝕤₂ = 𝐀₂*(gf⋅(T₂*𝕟ᶜⁿ))")   
p8 = plot!(𝕤𝕘[3].Dp,𝕤𝕘[3].N,  label = "𝕤₃ = 𝐀₂*(gf⋅(T₃*𝕟ᶜⁿ))")   
p8 = plot!(𝕤𝕘ₜ.Dp,𝕤𝕘ₜ.N, color = :black, ls = :dashdot, label = "𝕤ₜ=𝐀₂*∑(gf⋅(Tᵢ*𝕟ᶜⁿ))", left_margin = 31px)   

plot(p1,p2,p3,p4,p5,p6,p7,p8, layout = grid(4,2), right_margin = 30px, legend=:right, 
     top_margin = 15px,  xlim = (50, 500))

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 25. </b> Top left: input lognormal size distribution. Top right: response function as a function of diameter. Second row left: apparent +1 mobility distribution of classified aerosol, second row right: mobility distribution. Third row left: apparent +1 mobility distribution after passing through the humidification system. Third row right: mobility distribution after passing through the humidification system. Bottom left: apparent +1 mobility size distribution after passing through the second DMA without charge neutralization, bottom right: apparent +1 mobility size distribution after passing through the second DMA with a second charge neutralization step.

In the case where particles with known mobility are supplied to a second DMA and there is no bipolar charger,  function δ.Tc(k) is not used when computing the matrix. Since nothing is known about the particle mass/charge ratio, and the split within the population, all particles are assumed to be +1 charged. The only error in this assumption is that the multiply charged particles hiding in the mobility peak may have a different loss rate Tl, which does not vary strongly with size except for very small particles. To describe this process, the transmission matrix O is defined as
```julia
𝐎 = (hcat(map(i->Σ(k->δ.Ω(Λ,δ.Z,i/k).*δ.Tl(Λ,δ.Dp),1),δ.Z)...))'
```
which is similar to 𝐀 but with Λ.n = 1 and δ.Tc(k) omitted. The matrix 𝐎 is used to describe size selection in tandem DMA systems where no charge neutralization is used between DMA1 and DMA2.

In [88]:
𝐎 = (hcat(map(i->Σ(k->δ.Ω(Λ,δ.Z,i/k).*δ.Tl(Λ,δ.Dp),1),δ.Z)...))'

60×60 Adjoint{Float64,Array{Float64,2}}:
 0.950049     0.636955     0.28436      …  0.0          0.0        
 0.658172     0.949286     0.63682         0.0          0.0        
 0.36893      0.658041     0.948491        0.0          0.0        
 0.0981692    0.368857     0.657901        0.0          2.71376e-14
 4.057e-13    0.0981497    0.368778        0.0          0.0        
 0.0          1.61545e-12  0.098129     …  0.0          0.0        
 0.0          0.0          5.92033e-12     0.0          0.0        
 0.0          0.0          0.0             0.0          0.0        
 0.0          2.80535e-16  0.0             0.0          0.0        
 0.0          0.0          2.89889e-16     0.0          1.65412e-14
 0.0          0.0          0.0          …  0.0          0.0        
 0.0          0.0          0.0             1.77836e-14  0.0        
 0.0          0.0          0.0             0.0          0.0        
 ⋮                                      ⋱                          
 0.0   

### Growth Factor Distributions/TDMA Inversion
The above assumes that the particles have a single growth factor. For ambient data, growth factor is often distributed. The mobility response function after DMA2 without a second charge neutralization is rewritten as a function of gf. Also the convolution matrix O is folded into the function. Then let Pᵢ denote the probability that a particle has growth factor gfᵢ. A parametric distribution can be written as an array of P and an array of gf, subject to the constraint that sum(P) = 1. In this case the response function is computed as

```julia
y = sum(map(i->(P[i]*Nmdist(zˢ, gf[i])), 1:length(P)))
```

In [89]:
figure("Arial", 2, 2.5, 1.8, 8)

# Setup the special case
Dm = 100                 # Dry size 100 nm
zˢ = dtoz(Λ₁, Dm*1e-9);  # Compute corresponding electrical mobility
n = 3                    # Charges 1..3

Nmdist = (zˢ,gf) -> δ₂.𝐎*Σ(k->((ztod(Λ₁,1,zˢ)/ztod(Λ₁,k,zˢ))⋅(gf⋅(𝕥=T(zˢ,k,Λ₁,δ₁)*𝕟ᶜⁿ))),Λ₁.m)
#P = [0.5,0.15, 0.10, 0.25]   # Probability of growth factor (4 populations)
#gf = [1.0, 1.2, 1.6, 2.1]    # Values of growth factor

P = [0.5, 0.5]   # Probability of growth factor (1 compound)
gf = [1.0, 2.0]    # Values of growth factor

y = sum(map(i->(P[i]*Nmdist(zˢ, gf[i])), 1:length(P)))  # The growth factor distribution

plot(y.Dp/Dm, y.N, xlabel = "Growth factor (-)", ylabel = "Concentration (cm⁻³)", color = :black, 
     legend = :none, left_margin = 10px,  xlim = (0.7, 3), right_margin = 20px)

<!DOCTYPE html>
 
 
 Plots.jl

<b> Figure 26. </b> Predicted growth factor distribution for the four component model comprising gf = 1, 1.2, 1.6, and 2.1. The curve gives the response function normalized by the assumed dry diameter (100 nm) as predicted by the forward model O₂$*$(∑[(dᵢ$/$d₁)$⋅$(gf$⋅$(T₁$*$𝕟ᶜⁿ)))]). 

## (b) Volatility Tandem DMA

Figure 27 summarizes a typical volatility tandem DMA setup (VTMDA). Dried, charge equilibrated particles are classified in DMA 1. The flow is split to measure particle concentration with a condensation particle counter (CPC). The remaining flow is passed through an evaporation section, which is usually set at some temperature near or above ambient temperature. Particles evaporate controlled by evaporation kinetics and decrease in diameter. The evporated size distribution is measured using the second DMA that is operated in scanning or stepping mode. Passage through a second bipolar charger (charge neutralizer) is optional and rarely used in TDMA experiments.  <br>

<img src="Figures/nbs9_f01.png" width="750">

<figcaption><b> Figure 27. </b>  Schematic of a typical VTDMA setup. 
 </figcaption> 
 
 
In the HTDMA the particles are generally assumed to grow according to a diameter equilibrium growth factor. That growth factor is applied to all particle sizes. This assumption is usually valid for particles that have the same hygroscopicity, as the equilibrium growth factor only minimally depends on the particle size through the Kelvin effect. In the case of evaporation, the evaporation is usually controlled by evaporation kinetics. The kinetic evaporation rate is proportional to surface area and thus small particles decrease in diameter more rapidly than larger particles. The corresponding evaporation factor ef thus depends on particle size and evaporation time. Here evaporation is simulated using a simple model 
<center> $d_p \frac{dd_p}{dt} = g$ </center>
where $g$ is a factor that describes the evaporation rate. For real systems $g$ can be predicted from compound vapor pressures, mass and heat flux rates of the condensing/evaporting species, and the abundance of the species in the gas phase (e.g. Bilde et al. 2003, Xue et al. 2005, Wright et al. 2016). Here it is assumed that the particles are composed of a single component and that the evaporation rate is constant over time. The evaporation rate equation is integrated numerically for t = 10s to find the final diameter. The evaporation factor as a function of diameter is computed from $EF = \frac{D_{final}}{D_{initial}}$ for each particle diameter. The assumptions in the evporation model are not critical here. The main demonstration is how multiply charged particles will affect the observed VTDMA spectrum.

In [90]:
t,p = 295.15, 1e5                                # Temperature [K], Pressure [Pa]
qsa,β = 1.66e-5, 1/10                            # Qsample [m3 s-1], Sample-to-sheath ratio,
r₁,r₂,l = 9.37e-3,1.961e-2,0.44369               # DMA geometry [m]
leff = 13.0                                      # DMA effective diffusion length [m]
m = 3                                            # Upper number of charges
Λ₁ = DMAconfig(t,p,qsa,qsa/β,r₁,r₂,l,leff,:-,m,:cylindrical)  # Specify DMA with negative polarity
Λ₂ = DMAconfig(t,p,qsa,qsa/β,r₁,r₂,l,leff,:+,m,:cylindrical)  # Specify DMA with negative polarity
bins,z₁,z₂ = 512, dtoz(Λ₁,250e-9),dtoz(Λ₁,20e-9) # bins, upper, lower mobility limit
δ₁ = setupDMA(Λ₁, z₁, z₂, bins);                 # Compute matrices
δ₂ = setupDMA(Λ₂, z₁, z₂, bins);                 # Compute matrices

In [91]:
Dm = 100.0                      # Size select 100 nm mobility diameter
zˢ = dtoz(Λ₁, Dm*1e-9);         # Compute corresponding electrical mobility
T = (zˢ,k,Λ,δ) -> δ.Ω(Λ,δ.Z,zˢ/k).*δ.Tc(k,δ.Dp).*δ.Tl(Λ,δ.Dp); # Transfer model through DMA


Ax = [[400., 60., 1.5], [3000., 200., 1.6]]   # Assumed lognormal size distribution
𝕟ᶜⁿ = DMALognormalDistribution(Ax, δ₁)      

# Evaporation function
t = 10.0                     # Time for particles to evaporate [s]
dt = 1e-4                    # Timestep for evaporation - needs to be small for small sizes
g = -3.0e2
D = deepcopy(𝕟ᶜⁿ.Dp)
for i in 1:length(D)
    clock = 0                # Start the clock
    while clock < t
        D[i] = (D[i] < 10) ? D[i]-1e-11 : D[i] + g/D[i]*dt  # evaporate
        clock = clock + dt
    end
end
l  = length(D[D .< 10])      # Check for complete evaporation and fill the arry with dummy values 

D[end-l+1:end] = reverse(exp10.(range(log10(9.8), stop=log10(10), length=l)))
EF = D./𝕟ᶜⁿ.Dp;              # Compute the size depenent evaporation factor

In [92]:
T = (zˢ,k,Λ,δ) -> δ.Ω(Λ,δ.Z,zˢ/k).*δ.Tc(k,δ.Dp).*δ.Tl(Λ,δ.Dp) # Transfer model through DMA
Nkz = (zˢ,k,Λ,δ) -> EF⋅(𝕥=T(zˢ,k,Λ,δ)*𝕟ᶜⁿ)  # Size distribution for particles with charge k
Nz = (zˢ,Λ,δ) -> Σ(k->EF⋅(𝕥=T(zˢ,k,Λ,δ)*𝕟ᶜⁿ),Λ₁.m) # Total size distribution for all charges 1..n
Nkm = (zˢ,k,Λ,δ) -> ((ztod(Λ,1,zˢ)/ztod(Λ,k,zˢ))⋅(EF⋅(𝕥=T(zˢ,k,Λ,δ)*𝕟ᶜⁿ))) # App. Mobility dist k charges
Nm =(zˢ,Λ,δ) -> Σ(k->((ztod(Λ,1,zˢ)/ztod(Λ,k,zˢ))⋅(EF⋅(𝕥=T(zˢ,k,Λ,δ)*𝕟ᶜⁿ))),Λ₁.m); # Total all charges

In [93]:
# Setup the special case
Dm = 100                 # Dry size 100 nm
zˢ = dtoz(Λ₁, Dm*1e-9);  # Compute corresponding electrical mobility
n = 3                    # Charges 1..3

figure("Arial", 2, 5.5, 3.5, 8)
p = Plots.get_color_palette(:auto, default(:bgcolor), 100) # Get a list of colors from the theme palette

# Panel 1: m\Mobility diameter
𝕩 = map(k -> Nkz(zˢ,k,Λ₁,δ₁), 1:3)
𝕪 = Nz(zˢ,Λ₁,δ₁)
p1 = plot([ztod(Λ₁,1,zˢ), ztod(Λ₁,1,zˢ)], [0,200], color = p[1], ls = :dot, label = "D₁(zˢ)", lw = 2)
p1 = plot!([ztod(Λ₁,2,zˢ), ztod(Λ₁,2,zˢ)], [0,200], color = p[2], ls = :dot, label = "D₂(zˢ)", lw = 2)
p1 = plot!([ztod(Λ₁,3,zˢ), ztod(Λ₁,3,zˢ)], [0,200], color = p[3], ls = :dot, label = "D₃(zˢ)", lw = 2)
p1 = plot!(𝕩[1].Dp, 𝕩[1].S, label = "ℕ₁<sup>δ₁</sup>", xaxis = :log10, xlim = (50,500), color = p[1])
p1 = plot!(𝕩[2].Dp, 𝕩[2].S, label = "ℕ₂<sup>δ₁</sup>", color = p[2])
p1 = plot!(𝕩[3].Dp, 𝕩[3].S, label = "ℕ₃<sup>δ₁</sup>", color = p[3])
p1 = plot!(𝕪.Dp, 𝕪.S, color = :black, label = "𝕟ₜ<sup>δ₁</sup>", ls = :dashdot, lw = 1.25, 
    ylabel = "dN/dlnD (cm⁻³)", left_margin = 20px, xlabel = "Mobility Diameter (nm)")

# Panel 2: Apparent +1 Mobility diameter
𝕩 = map(k -> Nkm(zˢ,k,Λ₁,δ₁), 1:3)
𝕪 = Nm(zˢ,Λ₁,δ₁)
p2 = plot([ztod(Λ₁,1,zˢ), ztod(Λ₁,1,zˢ)], [0,200], color = :black, ls = :dot, label = "D₁(zˢ)", lw = 2)
p2 = plot!(𝕩[1].Dp, 𝕩[1].S, xlim = (120, 220), label = "𝕄₁<sup>δ₁</sup>", color = p[1])
p2 = plot!(𝕩[2].Dp, 𝕩[2].S, label = "𝕄₂<sup>δ₁</sup>", color = p[2])
p2 = plot!(𝕩[3].Dp, 𝕩[3].S, label = "𝕄₃<sup>δ₁</sup>", color = p[3])
p2 = plot!(𝕪.Dp, 𝕪.S, color = :black, lw = 1.25, ls = :dashdot,
     label = "𝕞ₜ<sup>δ₁</sup>", xlabel = "Apparent +1 Mobility Diameter (nm)")

# Panel 3: Passage through DMA
𝕩 = map(k -> δ₂.𝐀*Nkz(zˢ,k,Λ₁,δ₁), 1:3)
𝕪 = δ₂.𝐀*Nz(zˢ,Λ₁,δ₁)
p3 = plot(𝕩[1].Dp, 𝕩[1].N, label = "ℕ₁<sup>δ₂</sup>")
p3 = plot!(𝕩[2].Dp, 𝕩[2].N, label = "ℕ₂<sup>δ₂</sup>")
p3 = plot!(𝕩[3].Dp, 𝕩[3].N, label = "ℕ₃<sup>δ₂</sup>")
p3 = plot!(𝕪.Dp, 𝕪.N, xaxis = :log10,  ylim = (-0.1,2.5), xlim = (50,500), color = :black, ls = :dashdot,
            left_margin = 34px, lw = 1.25, label = "𝕟ₜ<sup>δ₂</sup>",
            ylabel = "Concentration (cm⁻³)", xlabel = "Apparent +1 Mobility Diameter (nm)")

# Panel 4: Passage through DMA
𝕩 = map(k -> δ₂.𝐎*Nkm(zˢ,k,Λ₁,δ₁), 1:3)
𝕪 = δ₂.𝐎*Nm(zˢ,Λ₁,δ₁)
p4 = plot(𝕩[1].Dp, 𝕩[1].N, label = "𝕄₁<sup>δ₂</sup>")
p4 = plot!(𝕩[2].Dp, 𝕩[2].N, label = "𝕄₂<sup>δ₂</sup>")
p4 = plot!(𝕩[3].Dp, 𝕩[3].N, label = "𝕄₃<sup>δ₂</sup>")
p4 = plot!(𝕪.Dp, 𝕪.N, xlim = (120,220), xlabel = "Apparent +1 Mobility Diameter (nm)", lw = 1.25, 
    ls = :dashdot, color = :black, left_margin = 30px, ylim = (0,9.5), label = "𝕞ₜ<sup>δ₂</sup>")

plot(p1,p2,p3,p4, layout = grid(2,2), legend=:right, xlim = (23,230),
     xaxis = :log10, top_margin = 35px, right_margin = 20px, lw = 2,
     bottom_margin = 20px)

<!DOCTYPE html>
 
 
 Plots.jl

__Figure 28.__ _Top left_. Evaporated mobility size distribution with +1 (blue), +2 (orange), and +3 (green) charges graphed at their physical diameter. Vertical dotted lines give the selected diameter by DMA1. The black dashdotted line gives the total distribution evaluated using the expression ∑[EF$.⋅$(Tᵢ$.*$𝕟ᶜⁿ)]. _Top right_. Apparent +1 mobility selected size. Blue, organge and green correspond to +1, +2, and +3 charges. Vertical dotted line is the selected mobility diameter by DMA1. Dashed line corresponds to the sum of the three evaluated with expression ∑[(dᵢ/d₁)$⋅$(EF$.⋅$(Tᵢ$.*$𝕟ᶜⁿ)))]. _Bottom left_. Same as top left after passage through a charge neutralizer and DMA2. Colors indicate the size distribution of +1 (blue), +2 (orange), and +3 (green) charges exiting DMA2. _Bottom right_. Apparent +1 mobility size distribution from panel above after passage through DMA2 without charge neutralization. Colors indicate the size distribution of +1 (blue), +2 (orange), and +3 (green) charges exiting DMA2. 

## References

Bilde, M., Svenningsson, B., Mønster, J., and Rosenørn, T. (2003). Even−Odd Alternation of Evaporation Rates and Vapor Pressures of C3−C9 Dicarboxylic Acid Aerosols. Environ. Sci. Technol., 37(7):1371–1378, DOI:10.1021/es0201810.

Collins, A. M.,  W. D. Dick & F. J. Romay (2013) A New Coincidence Correction Method for Condensation Particle Counters, Aerosol Science and Technology, 47:2, 177-182, DOI:10.1080/02786826.2012.737049

Cruz, C. N. and S. N. Pandis (1997). A study of the ability of pure secondary organic aerosol to act as cloud condensation nuclei. Atmospheric Environment 31, 2205–2214, DOI:10.1016/S1352-2310(97)00054-X.

Hansen, P. C. (2000) The L-Curve and its Use in the Numerical Treatment of Inverse Problems, in Computational Inverse Problems in Electrocardiology, ed. P. Johnston, Advances in Computational Bioengineering, 119-142, WIT Press. <br> 

Hagwood, C. (1999) The DMA Transfer Function with Brownian
Motion a Trajectory/Monte-Carlo Approach, Aerosol Science & Technology, 30:1, 40-61, DOI:10.1080/027868299304877.

Hinds, W. C. (1999) Aerosol Technology, Properties, Behavior, and Measurement of Airborne Particles, Second Edition, John Wiley & Sons, Inc.

Kandlikar, M., & Ramachandran, G. (1999) Inverse methods for analysing aerosol spectrometer measurements: A critical review. Journal of Aerosol Science, 30(4), 413-437, DOI: 10.1016/S0021-8502(98)00066-4. <br>

Knutson, E. O. & K. T. Whitby (1975) Aerosol classification by electric mobility:
Apparatus, theory, and applications. J. Aerosol Sci. (6)443-451, DOI:10.1016/0021-8502(75)90060-9.

Park, D. Dutcher, M. Emery, J. Pagels, H. Sakurai, J. Scheckman, S. Qian, M. R. Stolzenburg, X. Wang, J. Yang & P. H. McMurry (2008) Tandem Measurements of Aerosol Properties—A Review of Mobility Techniques with Extensions, Aerosol Science and Technology, 42:10, 801-816, DOI:10.1080/02786820802339561.
Snider, J. R., M. D. Petters, P. Wechsler, and P. S. K. Liu, (2006), Supersaturation in the Wyoming CCN instrument, Journal Atmospheric Oceanic Technology, 23, 1323-1339, doi:10.1175/JTECH1916.1. 

Petters, M. D., A. J. Prenni, S. M. Kreidenweis, P. J. DeMott (2007) On measuring the critical diameter of cloud condensation nuclei using mobility selected aerosol, Aerosol Science & Technology, 41(10), 907-913, doi:10.1080/02786820701557214.

Petters, M. D., C. M. Carrico, S. M. Kreidenweis, A. J. Prenni, P. J. DeMott, J. R. Collett Jr., and H. Moosmüller (2009) Cloud condensation nucleation ability of biomass burning aerosol, Journal Geophysical Research, 114, D22205, doi:10.1029/2009JD012353.

Petters, M. D. (2018) A language to simplify computation of differential mobility analyzer response functions, Aerosol Science & Technology, 52:12, 1437-1451, DOI: 10.1080/02786826.2018.1530724. 

Reineking A. & J. Porstendörfer (1986) Measurements of Particle Loss Functions in a Differential Mobility Analyzer (TSI, Model 3071) for Different Flow Rates, Aerosol Science and Technology, 5:4, 483-486, DOI:10.1080/02786828608959112

Saha, P. K., Khlystov, A., Yahya, K., Zhang, Y., Xu, L., Ng, N. L., and Grieshop, A. P.: Quantifying the volatility of organic aerosol in the southeastern US, Atmos. Chem. Phys., 17, 501-520, https://doi.org/10.5194/acp-17-501-2017, 2017. 

Rader, D.J. and P.H. McMurry (1986) Application of the tandem differential mobility analyzer to studies of droplet growth or evaporation,Journal of Aerosol Science, 17(5), 771-787,DOI:10.1016/0021-8502(86)90031-5.

Stolzenburg, M. R. & P. H. McMurry (2008) Equations Governing Single and Tandem DMA Configurations and a New Lognormal Approximation to the Transfer Function, Aerosol Science and Technology, 42:6, 421-432, DOI: 10.1080/02786820802157823.

Talukdar, Suddha S. & Mark T. Swihart (2010) An Improved Data Inversion Program for Obtaining Aerosol Size Distributions from Scanning Differential Mobility Analyzer Data, Aerosol Science and Technology, 37:2, 145-161, DOI: 10.1080/02786820300952. <br>

TSI Inc. (2009) Series 3080 Electrostatic Classifiers. Operation and Service Manual, P/N 1933792, Revision J March 2009. 

Wang, S. C. and Flagan, R. C. (1990). Scanning electrical mobility spectrometer.
Aerosol Science and Technology, 13:2, 230–240.

Wright, T. P., C. Song, S. Sears & M. D. Petters (2016) Thermodynamic and kinetic behavior of glycerol aerosol, Aerosol Science and Technology, 50:12, 1385-1396, DOI: 10.1080/02786826.2016.1245405.

Wiedensohler, A. (1988) An approximation of the bipolar charge distribution for particles in the submicron size range, Journal of Aerosol Science, 19:3, 387-389, DOI:10.1016/0021-8502(88)90278-9.

Xue, H., Moyle, A. M., Magee, N., Harrington, J. Y., and Lamb, D. (2005), Experimental Studies of Droplet Evaporation Kinetics: Validation of Models for Binary and Ternary Aqueous Solutions. J. Atmos. Sci., 62(12):4310–4326, DOI:10.1175/JAS3623.1.